In [1]:
pip install biom-format

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install scikit-bio

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install scikit-learn

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip uninstall xgboost -y

Found existing installation: xgboost 2.0.3
Uninstalling xgboost-2.0.3:
  Successfully uninstalled xgboost-2.0.3
Note: you may need to restart the kernel to use updated packages.


In [5]:
pip install xgboost==2.0.3


  Using cached xgboost-2.0.3-py3-none-macosx_12_0_arm64.whl.metadata (2.0 kB)
Using cached xgboost-2.0.3-py3-none-macosx_12_0_arm64.whl (1.9 MB)
Note: you may need to restart the kernel to use updated packages.


In [6]:
pip install imblearn

Note: you may need to restart the kernel to use updated packages.


In [7]:
pip install tensorflow

Note: you may need to restart the kernel to use updated packages.


In [8]:
pip install jinja2

Note: you may need to restart the kernel to use updated packages.


In [9]:
import warnings
warnings.filterwarnings('ignore')

# Core data manipulation
import pandas as pd
import numpy as np
from scipy import stats
from scipy.spatial.distance import pdist, squareform
from scipy.stats import mannwhitneyu, kruskal

# BIOM format handling
try:
    from biom import load_table
    from biom.util import biom_open
except ImportError:
    print("WARNING: biom-format not installed. Install with: pip install biom-format")

# Microbiome-specific libraries
try:
    from skbio.diversity import alpha_diversity, beta_diversity
    from skbio.stats.ordination import pcoa
    from skbio.stats.distance import permanova
except ImportError:
    print("WARNING: scikit-bio not installed. Install with: pip install scikit-bio")

# Machine Learning - sklearn
from sklearn.model_selection import (
    train_test_split, StratifiedKFold, cross_val_score,
    GridSearchCV, learning_curve
)
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.feature_selection import (
    VarianceThreshold, SelectKBest, f_classif, RFE, RFECV
)
from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score,
    roc_auc_score, confusion_matrix, classification_report,
    roc_curve, precision_recall_curve, matthews_corrcoef
)
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC

# Advanced ML models
import xgboost as xgb
import lightgbm as lgb

# Deep Learning
try:
    import tensorflow as tf
    from tensorflow import keras
    from tensorflow.keras import layers, callbacks
    from tensorflow.keras.models import Sequential
    from tensorflow.keras.layers import Dense, Dropout, BatchNormalization
except ImportError:
    print("WARNING: TensorFlow not installed. Install with: pip install tensorflow")

# Imbalanced learning
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from imblearn.pipeline import Pipeline as ImbPipeline

# Model interpretation
import shap

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.gridspec import GridSpec

# Utilities
import pickle
import joblib
from datetime import datetime
import os
import json

In [10]:
# DIAGNOSTIC FUNCTION - Inspect File Structure

def inspect_file_structure(filepath):
    """
    Inspect file structure to diagnose loading issues.

    Parameters:
    -----------
    filepath : str
        Path to file to inspect
    """
    print(f"\n{'='*80}")
    print(f"INSPECTING FILE: {filepath}")
    print(f"{'='*80}\n")

    try:
        with open(filepath, 'r') as f:
            lines = [next(f) for _ in range(5)]

        print("First 5 lines of file:")
        for i, line in enumerate(lines, 1):
            # Show first 150 characters of each line
            print(f"  Line {i}: {line[:150]}")
            if len(line) > 150:
                print(f"          ... (truncated, total length: {len(line)} chars)")

        # Count columns in header
        header = lines[0].strip().split('\t')
        print(f"\nHeader analysis:")
        print(f"  Number of columns: {len(header)}")
        print(f"  First 10 column names: {header[:10]}")

        # Check second line
        if len(lines) > 1:
            second_line = lines[1].strip().split('\t')
            print(f"\nSecond line analysis:")
            print(f"  Number of fields: {len(second_line)}")
            print(f"  First field (sample ID?): {second_line[0]}")

    except Exception as e:
        print(f"Error inspecting file: {e}")

    print(f"{'='*80}\n")

In [11]:
# Set random seeds for reproducibility
RANDOM_STATE = 42
np.random.seed(RANDOM_STATE)
tf.random.set_seed(RANDOM_STATE)

# Configure plotting style
plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette("husl")
plt.rcParams['figure.dpi'] = 300
plt.rcParams['savefig.dpi'] = 300
plt.rcParams['font.size'] = 10
plt.rcParams['figure.figsize'] = (10, 6)

# Create output directories
os.makedirs('results', exist_ok=True)
os.makedirs('results/figures', exist_ok=True)
os.makedirs('results/models', exist_ok=True)
os.makedirs('results/tables', exist_ok=True)

print("MICROBIOME MENTAL HEALTH CLASSIFIER - INITIALIZATION COMPLETE")
print(f"Random State: {RANDOM_STATE}")
print(f"Output Directory: ./results/")


MICROBIOME MENTAL HEALTH CLASSIFIER - INITIALIZATION COMPLETE
Random State: 42
Output Directory: ./results/


In [12]:
def load_microbiome_data(tsv_file, metadata_file, biom_file=None):
    """
    Load and integrate microbiome abundance data with metadata.
    FIXED VERSION with better sample ID matching
    """
    print("\n" + "="*80)
    print("PHASE 1: DATA LOADING & INTEGRATION")
    print("="*80)

    abundance_df = None

    # Try BIOM file first
    if biom_file:
        print(f"\n[1/3] Loading from BIOM file: {biom_file}...")
        try:
            biom_table = load_table(biom_file)
            abundance_df = biom_table.to_dataframe().T

            # CRITICAL FIX: Remove the .133467 suffix from ALL sample IDs
            abundance_df.index = abundance_df.index.str.replace('.133467', '', regex=False)

            print(f"✓ Loaded BIOM table: {abundance_df.shape[0]} samples × {abundance_df.shape[1]} features")
            print(f"  Sample IDs after cleanup (first 5): {list(abundance_df.index[:5])}")
        except Exception as e:
            print(f"⚠ BIOM loading failed: {e}")
            abundance_df = None

    # If BIOM failed, try TSV
    if abundance_df is None:
        print(f"\n[1/3] Loading from TSV file: {tsv_file}...")
        try:
            abundance_df = pd.read_csv(tsv_file, sep='\t', skiprows=1)
            first_col = abundance_df.columns[0]
            if first_col.startswith('#'):
                abundance_df.rename(columns={first_col: first_col.lstrip('#')}, inplace=True)
                abundance_df.set_index(first_col.lstrip('#'), inplace=True)
            else:
                abundance_df.set_index(abundance_df.columns[0], inplace=True)

            # Remove .133467 suffix
            abundance_df.columns = [str(col).replace('.133467', '') for col in abundance_df.columns]
            abundance_df = abundance_df.T

            print(f"✓ Loaded abundance table: {abundance_df.shape[0]} samples × {abundance_df.shape[1]} features")
        except Exception as e:
            print(f"✗ Error loading TSV: {e}")
            raise

    # Load metadata
    print(f"\n[2/3] Loading metadata from {metadata_file}...")
    metadata_df = pd.read_csv(metadata_file, sep='\t', index_col=0)
    if metadata_df.index.name and metadata_df.index.name.startswith('#'):
        metadata_df.index.name = metadata_df.index.name.lstrip('#')

    print(f"✓ Loaded metadata: {metadata_df.shape[0]} samples × {metadata_df.shape[1]} variables")

    # De-duplicate abundance_df
    if abundance_df.index.duplicated().any():
        dup_count = abundance_df.index.duplicated().sum()
        print(f"Warning: {dup_count} duplicate sample IDs in abundance data. Aggregating by sum.")
        abundance_df = abundance_df.groupby(level=0).sum()

    # De-duplicate metadata_df
    if metadata_df.index.duplicated().any():
        dup_count = metadata_df.index.duplicated().sum()
        print(f"Warning: {dup_count} duplicate sample IDs in metadata. Keeping first occurrence.")
        metadata_df = metadata_df[~metadata_df.index.duplicated(keep='first')]

    # Align samples
    print(f"\n[3/3] Aligning samples...")
    # Clean BIOM sample IDs to match metadata
    abundance_df.index = abundance_df.index.astype(str).str.replace(r'\.\d+$', '', regex=True)
    metadata_df.index = metadata_df.index.astype(str).str.strip()

    common_samples = abundance_df.index.intersection(metadata_df.index)
    print(f"  Common samples found: {len(common_samples)}")


    if len(common_samples) == 0:
        raise ValueError("No matching samples! Check sample ID formats.")

    abundance_df = abundance_df.loc[common_samples]
    metadata_df = metadata_df.loc[common_samples]

    print("\n" + "="*80)
    print(f"PHASE 1 COMPLETE: {len(common_samples)} samples × {abundance_df.shape[1]} features")
    print("="*80)

    return abundance_df, metadata_df

In [13]:
def identify_mental_health_variables(metadata_df):
    """
    Identify and extract mental health-related variables from metadata.

    Parameters:
    -----------
    metadata_df : DataFrame
        Sample metadata

    Returns:
    --------
    mental_health_df : DataFrame
        Extracted mental health variables
    target_variable : str
        Name of the primary target variable used for classification
    """
    print("\n" + "="*80)
    print("IDENTIFYING MENTAL HEALTH VARIABLES")
    print("="*80)

    # Search for mental health related columns
    mh_keywords = ['phq', 'gad', 'depression', 'anxiety', 'mental', 'mood',
                   'psych', 'diagnosed', 'antidepress', 'bipolar', 'schizophrenia',
                   'ptsd', 'anorexia', 'bulimia'] # Added more specific keywords

    mh_columns = []
    for col in metadata_df.columns:
        col_lower = col.lower()
        if any(keyword in col_lower for keyword in mh_keywords):
            mh_columns.append(col)

    print(f"\nFound {len(mh_columns)} potential mental health variables:")
    for col in mh_columns:
        print(f"  - {col}: {metadata_df[col].dtype}")
        if metadata_df[col].dtype == 'object':
            # Show value counts for object type to understand categories
            print(f"    Value counts:\n{metadata_df[col].value_counts().head()}")
        else:
            print(f"    Range: {metadata_df[col].min():.2f} - {metadata_df[col].max():.2f}")

    # Create binary target variable
    target_variable = None

    # Prioritize columns indicating a diagnosis or positive condition
    diagnosis_cols = [col for col in mh_columns if 'diagnos' in col.lower() or
                      'yes' in metadata_df[col].astype(str).str.lower().unique() or
                      'true' in metadata_df[col].astype(str).str.lower().unique()]

    # Look for a column that is likely a binary indicator ('yes'/'no', 0/1)
    binary_indicators = [col for col in diagnosis_cols if len(metadata_df[col].dropna().unique()) <= 5] # Look for few unique values

    # Try specific columns known to be potential binary targets in similar datasets
    potential_targets = ['mental_illness', 'mental_illness_type_depression',
                         'depression_diagnosis_phq9', 'mental_illness_type_anxiety',
                         'mental_illness_type_ptsd_posttraumatic_stress_disorder']

    for col in potential_targets:
        if col in metadata_df.columns:
             # Check if it contains 'yes'/'no' or 0/1 values
            unique_vals = metadata_df[col].dropna().astype(str).str.lower().unique()
            if ('yes' in unique_vals and 'no' in unique_vals) or ('1' in unique_vals and '0' in unique_vals):
                target_variable = col
                print(f"\n✓ Identified '{target_variable}' as a potential binary target variable.")
                break
            elif len(unique_vals) == 2: # Check if it's already binary with different labels
                 target_variable = col
                 print(f"\n✓ Identified '{target_variable}' as a potential binary target variable (2 unique values).")
                 break


    # If no obvious binary target found, try columns with scores (e.g., PHQ9, GAD7)
    if target_variable is None:
         score_cols = [col for col in mh_columns if 'score' in col.lower() or metadata_df[col].dtype in ['float64', 'int64']]
         if score_cols:
              target_variable = score_cols[0] # Take the first score column found
              print(f"\n No clear binary target found. Using '{target_variable}' as a potential continuous target variable.")


    if target_variable is None:
        print("\n ERROR: Could not identify a suitable mental health target variable in the metadata.")
        print("  Please check your metadata file for columns related to mental health diagnosis or scores.")
        # If no target variable is found, return the whole metadata and None for target
        return metadata_df[mh_columns] if mh_columns else metadata_df, None
    else:
         print(f"  Selected target variable: '{target_variable}'")
         # Return only the identified mental health columns and the selected target
         return metadata_df[mh_columns], target_variable


def create_target_labels(metadata_df, target_col, threshold=None):
    """
    Create binary classification labels from mental health scores or diagnoses.

    Parameters:
    -----------
    metadata_df : DataFrame
        Metadata containing mental health information
    target_col : str
        Column name for target variable
    threshold : float, optional
        Threshold for binarization (if continuous variable). If None and continuous,
        the median will be used.

    Returns:
    --------
    labels : Series
        Binary labels (0: healthy/negative, 1: mental health condition/positive)
        Returns None if target_col is not found or cannot be binarized.
    """
    print(f"\nCreating target labels from '{target_col}'...")

    if target_col is None or target_col not in metadata_df.columns:
        print(f"  Error: Target column '{target_col}' not found in metadata.")
        print(f"  Available columns: {list(metadata_df.columns)}")
        return None

    target_data = metadata_df[target_col].copy() # Work on a copy to avoid SettingWithCopyWarning

    # Handle 'not provided' or similar values
    target_data = target_data.replace(['not provided', 'not applicable', 'unknown'], np.nan)
    target_data = target_data.dropna() # Drop samples with no data for the target

    if target_data.empty:
        print(f"  Error: No valid data remaining in target column '{target_col}' after cleaning.")
        return None

    unique_vals = target_data.astype(str).str.lower().unique()
    print(f"  Unique values in target column: {unique_vals}")

    labels = None # Initialize labels

    # Case 1: Already binary (e.g., 'yes'/'no', 0/1)
    if 'yes' in unique_vals and 'no' in unique_vals:
        labels = target_data.apply(lambda x: 1 if str(x).lower() == 'yes' else 0 if str(x).lower() == 'no' else np.nan)
        labels = labels.dropna()
        print(f"  Binarized based on 'yes'/'no' values.")

    elif '1' in unique_vals and '0' in unique_vals:
         # Ensure values are treated as numbers if they are strings
         target_data_numeric = pd.to_numeric(target_data, errors='coerce').dropna()
         if not target_data_numeric.empty:
            labels = target_data_numeric.astype(int)
            print(f"  Binarized based on 0/1 values.")
         else:
            print("  Warning: Could not convert 0/1 values to numeric. Treating as categorical.")

    elif len(unique_vals) == 2:
         # Binary with other labels, attempt to map
         print(f"  Attempting to map binary labels: {unique_vals}")
         # Assuming one is positive and one is negative - need a robust way to determine which
         # For now, let's assume the more frequent one is negative (or requires more samples)
         value_counts = target_data.value_counts()
         if len(value_counts) == 2:
              negative_label = value_counts.index[0] # Assuming the most frequent is negative
              positive_label = value_counts.index[1]
              labels = target_data.apply(lambda x: 1 if x == positive_label else 0 if x == negative_label else np.nan)
              labels = labels.dropna()
              print(f"  Mapped labels: '{negative_label}' -> 0, '{positive_label}' -> 1")
         else:
              print(f"  Error: Could not map binary labels with counts: {value_counts.tolist()}")
              return None


    # Case 2: Continuous variable (e.g., score)
    elif target_data.dtype in ['float64', 'int64'] or pd.api.types.is_numeric_dtype(target_data):
        print("  Detected numeric target variable.")
        if threshold is None:
            # Use median as threshold for continuous scores if not provided
            threshold = target_data.median()
            print(f"  Using median ({threshold:.2f}) as binarization threshold.")

        labels = (target_data >= threshold).astype(int)
        print(f"  Binarized using threshold = {threshold:.2f}")

    # Case 3: Categorical (multiple unique values) - attempt to identify positive keywords
    elif target_data.dtype == 'object':
        print("  Detected categorical target variable. Attempting keyword matching.")
        positive_keywords = ['yes', 'true', 'depression', 'anxiety', 'diagnosed',
                             'bipolar', 'schizophrenia', 'ptsd', 'anorexia', 'bulimia']
        labels = target_data.apply(
            lambda x: 1 if any(kw in str(x).lower() for kw in positive_keywords) else 0
        )
        print(f"  Categorical encoding applied using keywords.")

    else:
        print(f"  Error: Cannot create binary labels from target column '{target_col}' of type {target_data.dtype}.")
        return None # Could not create labels

    # Ensure labels index is aligned with the original abundance/metadata data BEFORE dropping samples
    # Filter original metadata based on the index of the created labels
    aligned_metadata = metadata_df.loc[labels.index]
    aligned_abundance = abundance_df.loc[labels.index] # Need abundance_df from the outer scope

    # Now calculate the class distribution based on the potentially filtered labels
    class_counts = labels.value_counts()

    print(f"\n  Resulting Class Distribution (after dropping NaNs and samples):")
    if 0 in class_counts:
        print(f"    Negative (0): {class_counts[0]} ({class_counts[0]/len(labels)*100:.1f}%)")
    else:
        print(f"    Negative (0): 0 (0.0%)")

    if 1 in class_counts:
         print(f"    Positive (1): {class_counts[1]} ({class_counts[1]/len(labels)*100:.1f}%)")
    else:
        print(f"    Positive (1): 0 (0.0%)")

    if len(labels) < len(metadata_df):
        print(f"  Note: {len(metadata_df) - len(labels)} samples were dropped due to missing or unusable target variable data.")


    # Check for sufficient samples in each class
    if len(class_counts) < 2 or class_counts.min() < 10: # Arbitrary minimum threshold
        print("\n Warning: Resulting labels have insufficient samples in one or both classes for robust classification.")
        print("  Consider adjusting the target variable or threshold, or obtaining more data.")
        return None # Indicate that labels are unusable for classification


    return labels

In [14]:
def quality_control_filtering(abundance_df, metadata_df, min_reads=1000, min_prevalence=0.01,
                               min_abundance=0.000001, top_n_features=50):
    """
    Apply quality control filters to microbiome data and reduce feature space.
    """
    print("\n" + "="*80)
    print("PHASE 2: QUALITY CONTROL & PREPROCESSING")
    print("="*80)
    initial_samples = abundance_df.shape[0]
    initial_features = abundance_df.shape[1]
    print(f"\nInitial data dimensions:\n Samples: {initial_samples}\n Features: {initial_features}")
    # Convert to float32 to prevent integer overflow
    abundance_df = abundance_df.astype('float32')
    # Step 1: Filter samples by sequencing depth
    print(f"\n[1/3] Filtering samples with <{min_reads} reads...")
    sample_depths = abundance_df.sum(axis=1) # dtype removed
    samples_pass = sample_depths >= min_reads
    low_read_samples = abundance_df.index[~samples_pass]
    filtered_df = abundance_df.loc[samples_pass]
    metadata_df = metadata_df.drop(low_read_samples, errors='ignore') # <-- Add this line to align metadata
    print(f" Removed {(~samples_pass).sum()} samples, remaining {filtered_df.shape[0]}")
    # Step 2: Filter features by prevalence
    print(f"\n[2/3] Filtering features present in <{min_prevalence*100}% of samples...")
    prevalence = (filtered_df > 0).sum(axis=0) / filtered_df.shape[0]
    features_pass = prevalence >= min_prevalence
    filtered_df = filtered_df.loc[:, features_pass]
    print(f" Remaining features after prevalence filter: {filtered_df.shape[1]}")
    # Step 3: Filter by max relative abundance
    print(f"\n[3/3] Filtering features with <{min_abundance*100}% relative abundance...")
    rel_abundance = filtered_df.div(filtered_df.sum(axis=1), axis=0)
    max_rel_abundance = rel_abundance.max(axis=0)
    abundance_pass = max_rel_abundance >= min_abundance
    filtered_df = filtered_df.loc[:, abundance_pass]
    print(f" Remaining features after abundance filter: {filtered_df.shape[1]}")
    # Optional: Reduce to top N features by variance
    if top_n_features and filtered_df.shape[1] > top_n_features:
        top_features = filtered_df.var(axis=0).sort_values(ascending=False).head(top_n_features).index
        filtered_df = filtered_df.loc[:, top_features]
        print(f" Reduced to top {top_n_features} features by variance")
    qc_stats = {
        'initial_samples': initial_samples,
        'initial_features': initial_features,
        'filtered_samples': filtered_df.shape[0],
        'filtered_features': filtered_df.shape[1],
    }
    print(f"\nQC complete: {filtered_df.shape[0]} samples x {filtered_df.shape[1]} features retained")
    print("="*80)
    return filtered_df, metadata_df, qc_stats # <-- Update return to include metadata_df
# ----------------------------
# Normalize microbiome data
# ----------------------------
def normalize_microbiome_data(abundance_df, method='clr'):
    """
    Normalize microbiome abundance data.
    """
    print(f"\nNormalizing data using {method.upper()} method...")
    abundance_df = abundance_df.astype('float32') # avoid overflow
    if method.lower() == 'tss':
        normalized_df = abundance_df.div(abundance_df.sum(axis=1), axis=0)
    elif method.lower() == 'clr':
        pseudocount = 1
        abundance_pseudo = abundance_df + pseudocount
        geo_means = np.exp(np.log(abundance_pseudo).mean(axis=1))
        normalized_df = np.log(abundance_pseudo.div(geo_means, axis=0))
    elif method.lower() == 'log':
        pseudocount = 1
        normalized_df = np.log(abundance_df + pseudocount)
    else:
        raise ValueError(f"Unknown normalization method: {method}")
    print(f" Normalization complete")
    print(f" Data range: [{normalized_df.min().min():.3f}, {normalized_df.max().max():.3f}]")
    return normalized_df
# ----------------------------
# Create target labels
# ----------------------------
from sklearn.preprocessing import LabelEncoder
def create_target_labels(metadata_df, target_col='mental_illness'):
    """
    Create binary labels from metadata target variable.
    """
    print(f"\nCreating target labels from '{target_col}'...")
    if target_col not in metadata_df.columns:
        raise ValueError(f"Target column '{target_col}' not found in metadata")
    target_data = metadata_df[target_col].fillna("No") # treat missing as "No"
    # Use LabelEncoder for binary conversion
    le = LabelEncoder()
    labels = pd.Series(le.fit_transform(target_data), index=metadata_df.index)
    counts = labels.value_counts()
    print(f" Class distribution: {dict(counts)} (0: No, 1: Yes)")
    return labels

In [15]:
# =============================================================================
# PHASE 3: EXPLORATORY DATA ANALYSIS
# =============================================================================

def calculate_alpha_diversity(abundance_df):
    """Calculate alpha diversity metrics."""
    print("\nCalculating alpha diversity metrics...")

    metrics = {}

    # Shannon diversity
    def shannon(x):
        x = x[x > 0]
        if x.sum() == 0: # Handle samples with zero reads after filtering
             return 0.0
        props = x / x.sum()
        return -np.sum(props * np.log(props))

    metrics['shannon'] = abundance_df.apply(shannon, axis=1)

    # Simpson diversity
    def simpson(x):
        x = x[x > 0]
        if x.sum() == 0: # Handle samples with zero reads after filtering
            return 1.0 # Simpson index is 1 for a single species
        props = x / x.sum()
        return 1 - np.sum(props**2)

    metrics['simpson'] = abundance_df.apply(simpson, axis=1)

    # Observed features (richness)
    metrics['observed'] = (abundance_df > 0).sum(axis=1)

    print(f"  Calculated: Shannon, Simpson, Observed features")

    return pd.DataFrame(metrics)


def calculate_beta_diversity(abundance_df, metric='braycurtis'):
    """Calculate beta diversity distance matrix."""
    print(f"\nCalculating beta diversity ({metric})...")

    # Convert to relative abundance, handle potential zero sums after filtering
    sample_sums = abundance_df.sum(axis=1)
    # Avoid division by zero by adding a small epsilon or filtering samples with zero sum
    # Filter out samples with zero sum before calculating relative abundance and beta diversity
    valid_samples = sample_sums > 0
    if not valid_samples.all():
        print(f"  Warning: Removing {len(abundance_df) - valid_samples.sum()} samples with zero total reads for beta diversity calculation.")
        abundance_df = abundance_df[valid_samples]
        sample_sums = abundance_df.sum(axis=1)


    rel_abundance = abundance_df.div(sample_sums, axis=0)

    # Calculate pairwise distances
    distances = pdist(rel_abundance.values, metric=metric)
    distance_matrix = squareform(distances)

    distance_df = pd.DataFrame(
        distance_matrix,
        index=abundance_df.index,
        columns=abundance_df.index
    )

    print(f"  Distance matrix shape: {distance_df.shape}")

    return distance_df


def plot_eda_summary(abundance_df, metadata_df, labels, alpha_div, output_dir='results/figures'):
    """Generate comprehensive EDA visualizations with robust alignment and error handling."""
    print("\nGenerating EDA visualizations...")

    # Safety check for empty data
    if abundance_df.shape[1] == 0:
        print("  Warning: No features available for visualization. Skipping EDA plots.")
        return

    # Ensure labels index matches abundance_df index after any filtering
    common_samples_eda = abundance_df.index.intersection(labels.index)
    abundance_df_eda = abundance_df.loc[common_samples_eda]
    labels_eda = labels.loc[common_samples_eda]

    # Align alpha diversity with samples
    common_idx = alpha_div.index.intersection(labels_eda.index)
    alpha_div_eda_aligned = alpha_div.loc[common_idx]
    labels_eda_aligned = labels_eda.loc[common_idx]

    # Convert labels to numeric for plotting
    labels_numeric = pd.to_numeric(labels_eda_aligned, errors='coerce').fillna(0)

    fig = plt.figure(figsize=(20, 12))
    gs = GridSpec(3, 4, figure=fig, hspace=0.3, wspace=0.3)

    # 1. Class distribution
    ax1 = fig.add_subplot(gs[0, 0])
    class_counts = labels_eda.value_counts()
    if len(class_counts) > 0:
        colors = ['#2ecc71', '#e74c3c'] if len(class_counts) == 2 else ['#2ecc71']
        class_counts.plot(kind='bar', ax=ax1, color=colors)
        ax1.set_title('Class Distribution', fontweight='bold')
        ax1.set_xlabel('Class')
        ax1.set_ylabel('Count')
        if len(class_counts) == 2:
            ax1.set_xticklabels(['Healthy', 'Condition'], rotation=45)
        else:
            ax1.set_xticklabels(['All Samples (Single Class)'], rotation=45)
    else:
        ax1.text(0.5, 0.5, 'No class data', ha='center', va='center')
        ax1.set_title('Class Distribution', fontweight='bold')

    # 2. Sequencing depth
    ax2 = fig.add_subplot(gs[0, 1])
    sample_depths = abundance_df_eda.sum(axis=1)
    ax2.hist(sample_depths, bins=50, color='#3498db', edgecolor='black')
    ax2.set_title('Sequencing Depth Distribution', fontweight='bold')
    ax2.set_xlabel('Total Reads')
    ax2.set_ylabel('Frequency')
    ax2.axvline(sample_depths.median(), color='red', linestyle='--',
                label=f'Median: {sample_depths.median():.0f}')
    ax2.legend()

    # 3. Feature prevalence
    ax3 = fig.add_subplot(gs[0, 2])
    prevalence = (abundance_df_eda > 0).sum(axis=0) / len(abundance_df_eda)
    ax3.hist(prevalence, bins=50, color='#9b59b6', edgecolor='black')
    ax3.set_title('Feature Prevalence Distribution', fontweight='bold')
    ax3.set_xlabel('Prevalence (proportion of samples)')
    ax3.set_ylabel('Number of Features')

    # 4. Alpha diversity - Shannon
    ax4 = fig.add_subplot(gs[0, 3])
    unique_labels = labels_numeric.unique()
    plot_data = []
    positions = []
    labels_xticks = []

    for i, ul in enumerate(sorted(unique_labels)):
        group_shannon = alpha_div_eda_aligned.loc[labels_numeric == ul, 'shannon']
        if len(group_shannon) > 0:
            plot_data.append(group_shannon)
            positions.append(i)
            labels_xticks.append('Healthy' if ul == 0 else 'Condition')

    if plot_data:
        ax4.violinplot(plot_data, positions=positions, showmeans=True, showmedians=True)
        ax4.set_xticks(positions)
        ax4.set_xticklabels(labels_xticks)

        if len(plot_data) == 2:
            try:
                u_stat, p_val = mannwhitneyu(plot_data[0], plot_data[1], alternative='two-sided')
                ax4.text(0.5, 0.95, f'p = {p_val:.4f}', transform=ax4.transAxes,
                         ha='center', va='top', fontsize=9)
            except ValueError:
                pass
    else:
        ax4.text(0.5, 0.5, 'No data', ha='center', va='center')

    ax4.set_title('Shannon Diversity by Group', fontweight='bold')
    ax4.set_ylabel('Shannon Index')

    # 5. Top 20 feature heatmap
    ax5 = fig.add_subplot(gs[1, :])
    if abundance_df_eda.shape[1] > 0:
        rel_abundance = abundance_df_eda.div(abundance_df_eda.sum(axis=1) + 1e-10, axis=0)
        top_features = rel_abundance.mean().nlargest(20).index
        sorted_samples = labels_numeric.sort_values().index
        heatmap_data = rel_abundance.loc[sorted_samples, top_features].T
        sns.heatmap(heatmap_data, cmap='YlOrRd', ax=ax5, cbar_kws={'label': 'Relative Abundance'})
        ax5.set_title('Top 20 Features - Relative Abundance Heatmap', fontweight='bold', pad=20)
        ax5.set_xlabel('Samples (sorted by class)')
        ax5.set_ylabel('Features')
    else:
        ax5.text(0.5, 0.5, 'No features for heatmap', ha='center', va='center')
        ax5.set_title('Top 20 Features - Relative Abundance Heatmap', fontweight='bold', pad=20)

    # 6. Feature abundance distribution
    ax6 = fig.add_subplot(gs[2, 0:2])
    if abundance_df_eda.shape[1] > 0:
        rel_abundance = abundance_df_eda.div(abundance_df_eda.sum(axis=1) + 1e-10, axis=0)
        mean_abundance = rel_abundance.mean()
        ax6.scatter(range(len(mean_abundance)), np.sort(mean_abundance)[::-1],
                    alpha=0.6, s=10, color='#e67e22')
        ax6.set_yscale('log')
        ax6.set_title('Feature Abundance Distribution (Rank-Abundance)', fontweight='bold')
        ax6.set_xlabel('Feature Rank')
        ax6.set_ylabel('Mean Relative Abundance (log scale)')
        ax6.grid(True, alpha=0.3)
    else:
        ax6.text(0.5, 0.5, 'No features for plot', ha='center', va='center')
        ax6.set_title('Feature Abundance Distribution (Rank-Abundance)', fontweight='bold')

    # 7. Alpha diversity correlation
    ax7 = fig.add_subplot(gs[2, 2:])

    if len(alpha_div_eda_aligned) > 0:
    # Ensure perfect alignment between alpha diversity metrics and labels
        labels_numeric_aligned = labels_eda_aligned.reindex(alpha_div_eda_aligned.index)
        labels_numeric_aligned = pd.to_numeric(labels_numeric_aligned, errors='coerce').fillna(0)

    # Safety check: lengths must match
        if len(alpha_div_eda_aligned) != len(labels_numeric_aligned):
            print(f"⚠ Length mismatch: alpha_div ({len(alpha_div_eda_aligned)}), labels ({len(labels_numeric_aligned)})")
        # Align by dropping samples not present in both
            common_idx = alpha_div_eda_aligned.index.intersection(labels_numeric_aligned.index)
            alpha_div_plot = alpha_div_eda_aligned.loc[common_idx]
            labels_plot = labels_numeric_aligned.loc[common_idx]
        else:
            alpha_div_plot = alpha_div_eda_aligned
            labels_plot = labels_numeric_aligned

    # Only plot if we have data
        if len(alpha_div_plot) > 0:
            scatter = ax7.scatter(
            alpha_div_plot['shannon'],
            alpha_div_plot['simpson'],
            c=labels_plot,
            cmap='RdYlGn',
            alpha=0.6,
            s=50
            )
            ax7.set_title('Alpha Diversity Correlation', fontweight='bold')
            ax7.set_xlabel('Shannon Index')
            ax7.set_ylabel('Simpson Index')
            plt.colorbar(scatter, ax=ax7, label='Class')
        else:
            ax7.text(0.5, 0.5, 'No aligned data for correlation', ha='center', va='center')
            ax7.set_title('Alpha Diversity Correlation', fontweight='bold')
    else:
        ax7.text(0.5, 0.5, 'No data for correlation', ha='center', va='center')
        ax7.set_title('Alpha Diversity Correlation', fontweight='bold')


    plt.suptitle('Exploratory Data Analysis Summary', fontsize=16, fontweight='bold', y=0.995)
    plt.savefig(f'{output_dir}/eda_summary.png', dpi=300, bbox_inches='tight')
    plt.close()

    print(f"  EDA summary saved to {output_dir}/eda_summary.png")


In [16]:
# PHASE 4: DIFFERENTIAL ABUNDANCE ANALYSIS
# =============================================================================

def plot_volcano_plot(da_results, alpha=0.05, fc_threshold=1.0, output_dir='results/figures'):
    """
    Generate a volcano plot from differential abundance results.

    Parameters:
    -----------
    da_results : DataFrame
        Differential abundance results (from differential_abundance_analysis function)
    alpha : float
        Significance threshold (FDR-adjusted p-value)
    fc_threshold : float
        Log2 fold change threshold
    output_dir : str
        Output directory for figures
    """
    print("\nGenerating volcano plot...")

    # Check if da_results is empty or lacks necessary columns
    if da_results.empty or not all(col in da_results.columns for col in ['log2_fold_change', 'p_adjusted', 'significant']):
        print("  Skipping volcano plot: Differential abundance results are empty or missing required columns.")
        return

    # Ensure p_adjusted is numeric
    da_results['p_adjusted'] = pd.to_numeric(da_results['p_adjusted'], errors='coerce')
    da_results = da_results.dropna(subset=['p_adjusted']) # Drop rows where conversion failed

    # Create -log10(p_adjusted) column
    da_results['-log10_p_adjusted'] = -np.log10(da_results['p_adjusted'] + 1e-10) # Add epsilon for numerical stability


    plt.figure(figsize=(10, 8))
    sns.scatterplot(
        data=da_results,
        x='log2_fold_change',
        y='-log10_p_adjusted',
        hue='significant',
        palette={True: 'red', False: 'grey'},
        alpha=0.6,
        s=20
    )

    # Add lines for thresholds
    plt.axhline(-np.log10(alpha), color='grey', linestyle='--', label=f'FDR < {alpha}')
    plt.axvline(fc_threshold, color='grey', linestyle='--', label=f'|log2FC| > {fc_threshold}')
    plt.axvline(-fc_threshold, color='grey', linestyle='--')

    plt.xlabel('Log2 Fold Change', fontsize=12, fontweight='bold')
    plt.ylabel('-log10(Adjusted P-value)', fontsize=12, fontweight='bold')
    plt.title('Volcano Plot: Differential Abundance Analysis', fontsize=14, fontweight='bold')
    plt.legend(title='Significant')
    plt.grid(True, alpha=0.3)

    # Add labels for top features (optional)
    # Select top features based on significance and fold change
    top_features = da_results[
        (da_results['significant']) &
        (np.abs(da_results['log2_fold_change']) >= fc_threshold)
    ].nsmallest(10, 'p_adjusted') # Select top 10 by p-adjusted

    for i, row in top_features.iterrows():
        plt.text(row['log2_fold_change'], row['-log10_p_adjusted'], row['feature'][:15] + '...', fontsize=8)


    plt.tight_layout()
    plt.savefig(f'{output_dir}/volcano_plot.png', dpi=300, bbox_inches='tight')
    plt.close()

    print(f"  Volcano plot saved to {output_dir}/volcano_plot.png")


def differential_abundance_analysis(abundance_df, labels, alpha=0.05):
    """
    Perform differential abundance testing between groups.

    Parameters:
    -----------
    abundance_df : DataFrame
        Normalized abundance data
    labels : Series
        Binary class labels
    alpha : float
        Significance threshold for FDR correction

    Returns:
    --------
    da_results : DataFrame
        Differential abundance results with statistics
    """
    print("\n" + "="*80)
    print("PHASE 4: DIFFERENTIAL ABUNDANCE ANALYSIS")
    print("="*80)

    print("\nPerforming Mann-Whitney U tests for each feature...")

    results = []

    # Ensure labels are aligned with abundance_df index before iterating
    common_samples = abundance_df.index.intersection(labels.index)
    abundance_df_aligned = abundance_df.loc[common_samples]
    labels_aligned = labels.loc[common_samples]

    # Check if both classes are present after alignment
    if len(labels_aligned.unique()) < 2:
        print("\n Warning: Only one class present after aligning data and labels. Cannot perform differential abundance analysis.")
        # Create an empty DataFrame with expected columns, ensuring numeric dtypes where possible
        return pd.DataFrame(columns=['feature', 'mean_healthy', 'mean_condition',
                                     'log2_fold_change', 'cohens_d', 'p_value',
                                     'u_statistic', 'p_adjusted', 'significant'])


    for feature in abundance_df_aligned.columns:
        # Get data for each group
        group0 = abundance_df_aligned.loc[labels_aligned[labels_aligned == 0].index, feature]
        group1 = abundance_df_aligned.loc[labels_aligned[labels_aligned == 1].index, feature]

        # Mann-Whitney U test
        try:
            # Ensure there are enough samples in each group for the test
            if len(group0) > 0 and len(group1) > 0:
                # Ensure there is variance within at least one group
                if group0.std() > 1e-9 or group1.std() > 1e-9: # Use small tolerance for floating point
                     u_stat, p_value = mannwhitneyu(group0, group1, alternative='two-sided')

                     # Calculate effect size (Cohen's d)
                     mean0, mean1 = group0.mean(), group1.mean()
                     std_pooled = np.sqrt(((len(group0)-1)*group0.std()**2 + (len(group1)-1)*group1.std()**2) / (len(group0) + len(group1) - 2))
                     cohens_d = (mean1 - mean0) / std_pooled if std_pooled > 0 else 0

                     # Log2 fold change
                     log2fc = np.log2((mean1 + 1e-10) / (mean0 + 1e-10)) # Add epsilon for numerical stability

                     results.append({
                         'feature': feature,
                         'mean_healthy': mean0,
                         'mean_condition': mean1,
                         'log2_fold_change': log2fc,
                         'cohens_d': cohens_d,
                         'p_value': p_value,
                         'u_statistic': u_stat
                     })
                else:
                    # print(f"  Skipping feature {feature}: Zero variance in both groups.")
                    pass # Skip features with zero variance in both groups
            else:
                 # print(f"  Skipping feature {feature}: Not enough samples in one or both groups.")
                 pass # Skip features where one or both groups are empty

        except Exception as e:
            # print(f"  Error testing feature {feature}: {e}")
            continue # Skip features that cause other errors during testing

    da_results = pd.DataFrame(results)

    # Check if any results were generated before FDR correction
    if da_results.empty:
        print("\n Warning: No features passed differential abundance testing criteria.")
        print("  Possible reasons: Data too sparse, insufficient samples per group, or zero variance within groups.")
        # Return empty DataFrame with expected columns, ensuring numeric dtypes where possible
        return pd.DataFrame(columns=['feature', 'mean_healthy', 'mean_condition',
                                     'log2_fold_change', 'cohens_d', 'p_value',
                                     'u_statistic', 'p_adjusted', 'significant'])


    # FDR correction (Benjamini-Hochberg)
    from statsmodels.stats.multitest import multipletests
    # Check if 'p_value' column exists and is not empty before correction
    if 'p_value' in da_results.columns and not da_results['p_value'].empty:
        _, p_adjusted, _, _ = multipletests(da_results['p_value'], alpha=alpha, method='fdr_bh')
        da_results['p_adjusted'] = p_adjusted
        da_results['significant'] = da_results['p_adjusted'] < alpha
    else:
         print("\n⚠ Skipping FDR correction: No p-values available.")
         # Add placeholder columns with default values/dtypes if correction is skipped
         da_results['p_adjusted'] = np.nan
         da_results['significant'] = False


    # Sort by p-adjusted value, then by p-value if adjusted are equal
    # Only attempt sort if 'p_adjusted' column exists
    if 'p_adjusted' in da_results.columns:
         da_results = da_results.sort_values(['p_adjusted', 'p_value'])


    print(f"\n Differential abundance analysis complete")
    print(f"  Total features tested: {len(da_results)}")
    if 'significant' in da_results.columns:
         print(f"  Significant features (FDR < {alpha}): {da_results['significant'].sum()}")
    else:
         print("  Significant features count not available (FDR correction skipped).")

    print(f"\nTop 10 differentially abundant features:")
    if not da_results.empty and 'p_adjusted' in da_results.columns:
        print(da_results.head(10)[['feature', 'log2_fold_change', 'cohens_d', 'p_adjusted']])
    else:
        print("  No significant features found or results table is empty.")


    return da_results

In [17]:
# PHASE 5-6: FEATURE ENGINEERING & SELECTION
# =============================================================================

def engineer_features(abundance_df, alpha_div):
    """
    Create additional features from microbiome data.

    Parameters:
    -----------
    abundance_df : DataFrame
        Normalized abundance data
    alpha_div : DataFrame
        Alpha diversity metrics

    Returns:
    --------
    feature_df : DataFrame
        Enhanced feature matrix
    """
    print("\n" + "="*80)
    print("PHASE 5: ADVANCED FEATURE ENGINEERING")
    print("="*80)

    print("\n[1/4] Starting with base features...")
    # Convert abundance_df to dense format if it's sparse
    if any(pd.api.types.is_sparse(abundance_df[col].dtype) for col in abundance_df.columns):
        print("  Converting abundance data from sparse to dense format...")
        abundance_df_dense = abundance_df.sparse.to_dense()
    else:
        abundance_df_dense = abundance_df.copy() # Work on a copy


    feature_df = abundance_df_dense.copy()
    print(f"  Base features: {feature_df.shape[1]}")

    # Add alpha diversity metrics
    print("\n[2/4] Adding alpha diversity features...")
    # Ensure alpha_div is aligned with abundance_df_dense
    common_samples = abundance_df_dense.index.intersection(alpha_div.index)
    alpha_div_aligned = alpha_div.loc[common_samples]

    for col in alpha_div_aligned.columns:
        feature_df[f'alpha_div_{col}'] = alpha_div_aligned[col]
    print(f"  Added {len(alpha_div_aligned.columns)} alpha diversity features")


    # Add taxonomic ratios (if possible to identify phyla)
    print("\n[3/4] Creating taxonomic ratio features...")
    # Example: Firmicutes/Bacteroidetes ratio
    # This requires taxonomic information - placeholder for now
    # Use the dense abundance data for relative abundance calculation
    if not abundance_df_dense.empty and abundance_df_dense.sum(axis=1).min() > 0:
        rel_abundance = abundance_df_dense.div(abundance_df_dense.sum(axis=1), axis=0)

        # Create top taxa ratios
        # Check if rel_abundance is not empty before calculating mean
        if not rel_abundance.empty:
            mean_rel_abundance = rel_abundance.mean()
            # Check if mean_rel_abundance is not empty before finding top features
            if not mean_rel_abundance.empty:
                top_features = mean_rel_abundance.nlargest(20).index

                for i in range(min(5, len(top_features))):
                    for j in range(i+1, min(5, len(top_features))):
                        feat1, feat2 = top_features[i], top_features[j]
                        ratio_name = f'ratio_{feat1[:20]}_to_{feat2[:20]}'
                        # Add a small epsilon to denominators to avoid division by zero
                        feature_df[ratio_name] = (rel_abundance[feat1] + 1e-10) / (rel_abundance[feat2] + 1e-10)
            else:
                 print("  Skipping taxonomic ratios: Mean relative abundance is empty.")

        else:
             print("  Skipping taxonomic ratios: Relative abundance data is empty.")

    else:
        print("  Skipping taxonomic ratios: Dense abundance data is empty or has zero sum samples.")


    print(f"  Created taxonomic ratio features")

    # Add statistical features
    print("\n[4/4] Adding statistical summary features...")
    # Perform calculations on the dense dataframe
    if not abundance_df_dense.empty:
        feature_df['total_abundance'] = abundance_df_dense.sum(axis=1)
        feature_df['feature_count'] = (abundance_df_dense > 0).sum(axis=1)
        feature_df['max_abundance'] = abundance_df_dense.max(axis=1)
        feature_df['mean_abundance'] = abundance_df_dense.mean(axis=1)
        feature_df['std_abundance'] = abundance_df_dense.std(axis=1)
    else:
         print("  Skipping statistical features: Dense abundance data is empty.")


    print(f"\n✓ Feature engineering complete")
    print(f"  Final feature count: {feature_df.shape[1]}")
    print("="*80)

    return feature_df


def select_features(X, y, method='combined', k=100):
    """
    Perform feature selection using multiple methods.

    Parameters:
    -----------
    X : DataFrame
        Feature matrix
    y : Series
        Target labels
    method : str
        Selection method: 'variance', 'univariate', 'rfe', 'combined'
    k : int
        Number of features to select

    Returns:
    --------
    selected_features : list
        Names of selected features
    X_selected : DataFrame
        Selected feature matrix
    """
    print("\n" + "="*80)
    print("PHASE 6: FEATURE SELECTION")
    print("="*80)

    print(f"\nInitial features: {X.shape[1]}")
    print(f"Target selection: {k} features\n")

    # Ensure X and y are aligned
    common_samples = X.index.intersection(y.index)
    X_aligned = X.loc[common_samples].copy() # Work on a copy


    y_aligned = y.loc[common_samples]

    if X_aligned.empty or y_aligned.empty:
        print("\n Warning: Empty data after aligning features and labels. Skipping feature selection.")
        return [], pd.DataFrame() # Return empty lists/DataFrames

    # Explicitly convert X_aligned to dense format regardless of initial state
    # Use astype(float) which handles sparse to dense conversion implicitly
    try:
        X_aligned_dense = X_aligned.astype(float)
        print("  Converted aligned feature matrix to dense (float) format for selection.")
    except Exception as e:
        print(f"   Error converting aligned feature matrix to dense float: {e}")
        print("  Attempting alternative conversion...")
        # Fallback to sparse.to_dense() if astype(float) fails
        if any(pd.api.types.is_sparse(X_aligned[col].dtype) for col in X_aligned.columns):
            try:
                 X_aligned_dense = X_aligned.sparse.to_dense()
                 print("  Converted aligned feature matrix using sparse.to_dense().")
            except Exception as e2:
                 print(f"   Error converting aligned feature matrix using sparse.to_dense(): {e2}")
                 print("  Skipping feature selection due to conversion failure.")
                 return [], pd.DataFrame()
        else:
            # If not sparse and astype(float) failed, something else is wrong
            print("   Aligned feature matrix is not sparse, but conversion to float failed.")
            print("  Skipping feature selection due to conversion failure.")
            return [], pd.DataFrame()


    selected_features = []

    if method == 'variance' or method == 'combined':
        print("[1/3] Variance threshold filtering...")
        # Check if X_aligned_dense has variance before applying VarianceThreshold
        if X_aligned_dense.var().sum() > 1e-9:
            selector = VarianceThreshold(threshold=0.01)
            selector.fit(X_aligned_dense)
            var_features = X_aligned_dense.columns[selector.get_support()].tolist()
            print(f"  Features passing variance threshold: {len(var_features)}")
            selected_features.extend(var_features)
        else:
             print("  Skipping variance threshold: Data has zero variance.")


    if method == 'univariate' or method == 'combined':
        print("\n[2/3] Univariate feature selection (ANOVA F-test)...")
        # Check if X_aligned_dense has features and y_aligned has more than one class before applying SelectKBest
        if X_aligned_dense.shape[1] > 0 and len(y_aligned.unique()) > 1:
            try:
                selector = SelectKBest(f_classif, k=min(k, X_aligned_dense.shape[1]))
                selector.fit(X_aligned_dense, y_aligned)
                uni_features = X_aligned_dense.columns[selector.get_support()].tolist()
                print(f"  Top {len(uni_features)} univariate features selected")
                selected_features.extend(uni_features)
            except ValueError as e:
                 print(f"  Skipping univariate selection: Could not perform f_classif. Error: {e}")
            except Exception as e:
                 print(f"  Skipping univariate selection due to unexpected error: {e}")

        else:
             print("  Skipping univariate selection: Insufficient features or single class.")


    if method == 'rfe' or method == 'combined':
        print("\n[3/3] Recursive Feature Elimination...")
        # Check if X_aligned_dense has features and y_aligned has more than one class before applying RFE
        if X_aligned_dense.shape[1] > 0 and len(y_aligned.unique()) > 1:
            try:
                # Limit n_features_to_select to be less than or equal to the number of features in X_aligned_dense
                n_features = min(k, X_aligned_dense.shape[1])
                if n_features > 0:
                    # Ensure n_features_to_select is less than or equal to the number of features
                    if n_features > X_aligned_dense.shape[1]:
                        n_features = X_aligned_dense.shape[1]
                        print(f"  Adjusted n_features_to_select for RFE to match available features: {n_features}")


                    estimator = RandomForestClassifier(n_estimators=50, random_state=RANDOM_STATE, n_jobs=-1)
                    # Adjust step based on feature count, ensure step is at least 1
                    step_size = max(1, min(10, n_features // 5))
                    selector = RFE(estimator, n_features_to_select=n_features, step=step_size)
                    selector.fit(X_aligned_dense, y_aligned)
                    rfe_features = X_aligned_dense.columns[selector.get_support()].tolist()
                    print(f"  Top {len(rfe_features)} RFE features selected")
                    selected_features.extend(rfe_features)
                else:
                     print("  Skipping RFE: No features to select.")

            except ValueError as e:
                 print(f"  Skipping RFE: Could not perform RFE. Error: {e}")
            except Exception as e:
                 print(f"  Skipping RFE due to unexpected error: {e}")
        else:
             print("  Skipping RFE: Insufficient features or single class.")


    # Combine and get unique features
    if method == 'combined':
        from collections import Counter
        feature_counts = Counter(selected_features)
        # Select features that appear in at least 1 method initially
        selected_features_combined = [f for f, count in feature_counts.items() if count >= 1]

        if len(selected_features_combined) < k:
            # If fewer than k features selected by at least one method,
            # take the top k features based on total count across methods
            all_features_by_count = [f for f, _ in feature_counts.most_common(k)]
            selected_features_combined = all_features_by_count[:k]

        selected_features = list(set(selected_features_combined))[:k]
    else:
         # For non-combined methods, just ensure uniqueness and limit to k
         selected_features = list(set(selected_features))[:k]


    X_selected = X_aligned_dense[selected_features]

    print(f"\n Feature selection complete")
    print(f"  Selected features: {len(selected_features)}")
    print(f"  Final feature matrix shape: {X_selected.shape}")
    print("="*80)

    return selected_features, X_selected

In [18]:
# PHASE 7-8: MACHINE LEARNING MODEL DEVELOPMENT & OPTIMIZATION
# =============================================================================

# ------------------------------
# 0️⃣ Utility function: align X and y
# ------------------------------

def align_features_labels(X, y):
    """
    Align features (X) and labels (y) by common index.
    Handles duplicate indices by keeping only unique samples.
    """
    print(f"\nAligning features and labels...")
    print(f"  Initial X shape: {X.shape}, unique indices: {X.index.nunique()}")
    print(f"  Initial y shape: {y.shape}, unique indices: {y.index.nunique()}")
    
    # CRITICAL: Remove duplicates FIRST
    if X.index.duplicated().any():
        n_dupes = X.index.duplicated().sum()
        print(f"  ⚠ Removing {n_dupes} duplicate indices from X")
        X = X[~X.index.duplicated(keep='first')]
    
    if y.index.duplicated().any():
        n_dupes = y.index.duplicated().sum()
        print(f"  ⚠ Removing {n_dupes} duplicate indices from y")
        y = y[~y.index.duplicated(keep='first')]
    
    # Find common sample IDs
    common_samples = X.index.intersection(y.index)
    
    if len(common_samples) == 0:
        raise ValueError("No common sample IDs found between X and y!")
    
    n_dropped_x = len(X) - len(common_samples)
    n_dropped_y = len(y) - len(common_samples)
    
    if n_dropped_x > 0 or n_dropped_y > 0:
        print(f"  ⚠ Dropping samples to align:")
        print(f"    From X: {n_dropped_x}")
        print(f"    From y: {n_dropped_y}")
    
    # Align to common samples
    X_aligned = X.loc[common_samples]
    y_aligned = y.loc[common_samples]
    
    # Final verification
    assert X_aligned.shape[0] == y_aligned.shape[0], \
        f"Alignment failed: X has {X_aligned.shape[0]}, y has {y_aligned.shape[0]}"
    assert X_aligned.index.equals(y_aligned.index), \
        "Index mismatch after alignment"
    
    print(f"  ✓ Successfully aligned: {len(common_samples)} samples")
    
    return X_aligned, y_aligned


def prepare_train_test_split(X, y, test_size=0.15, val_size=0.15):
    """
    Split data into train/validation/test with stratification.
    Aligns X and y automatically to prevent mismatched sample errors.
    """
    from sklearn.model_selection import train_test_split
    from imblearn.over_sampling import SMOTE
    
    print("\nPreparing train/validation/test splits...")
    
    # ALIGN HERE - this now handles duplicates properly
    X_aligned, y_aligned = align_features_labels(X, y)
    
    # First split: separate test set
    X_temp, X_test, y_temp, y_test = train_test_split(
        X_aligned, y_aligned,
        test_size=test_size,
        random_state=RANDOM_STATE,
        stratify=y_aligned
    )
    
    # Second split: separate validation from training
    val_size_adjusted = val_size / (1 - test_size)
    X_train, X_val, y_train, y_val = train_test_split(
        X_temp, y_temp,
        test_size=val_size_adjusted,
        random_state=RANDOM_STATE,
        stratify=y_temp
    )
    
    print(f"\nSplit sizes:")
    print(f"  Training:   {X_train.shape[0]} samples ({X_train.shape[0]/len(X_aligned)*100:.1f}%)")
    print(f"  Validation: {X_val.shape[0]} samples ({X_val.shape[0]/len(X_aligned)*100:.1f}%)")
    print(f"  Test:       {X_test.shape[0]} samples ({X_test.shape[0]/len(X_aligned)*100:.1f}%)")
    
    # Check class distribution before SMOTE
    print(f"\nClass distribution before SMOTE:")
    print(f"  Training:   {dict(y_train.value_counts())}")
    print(f"  Validation: {dict(y_val.value_counts())}")
    print(f"  Test:       {dict(y_test.value_counts())}")
    
    # SMOTE to balance training classes
    print("\nApplying SMOTE to balance training set...")
    smote = SMOTE(random_state=RANDOM_STATE)
    X_train_bal, y_train_bal = smote.fit_resample(X_train, y_train)
    
    print(f"  After SMOTE: {dict(pd.Series(y_train_bal).value_counts())}")
    
    return {
        'X_train': X_train_bal,
        'y_train': y_train_bal,
        'X_val': X_val,
        'y_val': y_val,
        'X_test': X_test,
        'y_test': y_test,
        'n_dropped': len(X) - len(X_aligned)
    }

def train_xgboost_model(X_train, y_train, X_val, y_val):
    """
    Train and optimize XGBoost classifier.

    Parameters:
    -----------
    X_train : DataFrame
        Training features
    y_train : Series
        Training labels
    X_val : DataFrame
        Validation features
    y_val : Series
        Validation labels

    Returns:
    --------
    best_model : XGBoost classifier
        Optimized model
    best_params : dict
        Best hyperparameters
    """
    print("\n" + "="*80)
    print("PHASE 7: TRAINING XGBOOST MODEL")
    print("="*80)

    print("\n[1/2] Hyperparameter tuning with GridSearchCV...")

    # Define parameter grid
    param_grid = {
        'max_depth': [3, 5, 7],
        'learning_rate': [0.01, 0.05, 0.1],
        'n_estimators': [100, 200, 300],
        'subsample': [0.8, 1.0],
        'colsample_bytree': [0.8, 1.0],
        'min_child_weight': [1, 3],
    }

    # Initialize base model
    xgb_model = xgb.XGBClassifier(
        objective='binary:logistic',
        random_state=RANDOM_STATE,
        use_label_encoder=False,
        eval_metric='logloss'
    )

    # Grid search with cross-validation
    grid_search = GridSearchCV(
        estimator=xgb_model,
        param_grid=param_grid,
        cv=StratifiedKFold(n_splits=5, shuffle=True, random_state=RANDOM_STATE),
        scoring='roc_auc',
        n_jobs=-1,
        verbose=1
    )

    print("  Running grid search (this may take several minutes)...")
    grid_search.fit(X_train, y_train)

    best_params = grid_search.best_params_
    print(f"\n  Best parameters found:")
    for param, value in best_params.items():
        print(f"    {param}: {value}")
    print(f"  Best CV score: {grid_search.best_score_:.4f}")

    print("\n[2/2] Training final model with best parameters...")
    best_model = grid_search.best_estimator_

    # Evaluate on validation set
    y_val_pred = best_model.predict(X_val)
    y_val_proba = best_model.predict_proba(X_val)[:, 1]

    val_accuracy = accuracy_score(y_val, y_val_pred)
    val_auc = roc_auc_score(y_val, y_val_proba)

    print(f"\n  Validation Performance:")
    print(f"    Accuracy: {val_accuracy:.4f}")
    print(f"    AUC-ROC: {val_auc:.4f}")

    print("="*80)

    return best_model, best_params


def train_neural_network(X_train, y_train, X_val, y_val, epochs=100):
    """
    Train feedforward neural network.

    Parameters:
    -----------
    X_train : DataFrame
        Training features
    y_train : Series
        Training labels
    X_val : DataFrame
        Validation features
    y_val : Series
        Validation labels
    epochs : int
        Maximum training epochs

    Returns:
    --------
    model : Keras model
        Trained neural network
    history : History object
        Training history
    """
    print("\n" + "="*80)
    print("PHASE 7: TRAINING NEURAL NETWORK")
    print("="*80)

    print("\n[1/3] Building neural network architecture...")

    # Scale features
    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)
    X_val_scaled = scaler.transform(X_val)

    # Build model
    model = Sequential([
        Dense(256, activation='relu', input_dim=X_train.shape[1]),
        BatchNormalization(),
        Dropout(0.3),

        Dense(128, activation='relu'),
        BatchNormalization(),
        Dropout(0.3),

        Dense(64, activation='relu'),
        BatchNormalization(),
        Dropout(0.2),

        Dense(1, activation='sigmoid')
    ])

    model.compile(
        optimizer=keras.optimizers.Adam(learning_rate=0.001),
        loss='binary_crossentropy',
        metrics=['accuracy', keras.metrics.AUC(name='auc')]
    )

    print(f"  Model architecture:")
    model.summary()

    print("\n[2/3] Training model...")

    # Callbacks
    early_stop = callbacks.EarlyStopping(
        monitor='val_auc',
        patience=15,
        restore_best_weights=True,
        mode='max'
    )

    reduce_lr = callbacks.ReduceLROnPlateau(
        monitor='val_loss',
        factor=0.5,
        patience=5,
        min_lr=1e-6
    )

    # Train model
    history = model.fit(
        X_train_scaled, y_train,
        validation_data=(X_val_scaled, y_val),
        epochs=epochs,
        batch_size=32,
        callbacks=[early_stop, reduce_lr],
        verbose=1
    )

    print("\n[3/3] Evaluating on validation set...")
    val_loss, val_accuracy, val_auc = model.evaluate(X_val_scaled, y_val, verbose=0)

    print(f"\n  Validation Performance:")
    print(f"    Accuracy: {val_accuracy:.4f}")
    print(f"    AUC-ROC: {val_auc:.4f}")
    print(f"    Loss: {val_loss:.4f}")

    print("="*80)

    return model, history, scaler


def train_additional_models(X_train, y_train, X_val, y_val):
    """Train additional ML models for comparison."""
    print("\n" + "="*80)
    print("TRAINING ADDITIONAL MODELS FOR COMPARISON")
    print("="*80)

    models = {}

    # Random Forest
    print("\n[1/4] Training Random Forest...")
    rf_model = RandomForestClassifier(
        n_estimators=200,
        max_depth=10,
        min_samples_split=5,
        random_state=RANDOM_STATE,
        n_jobs=-1
    )
    rf_model.fit(X_train, y_train)
    y_val_pred = rf_model.predict(X_val)
    y_val_proba = rf_model.predict_proba(X_val)[:, 1]
    print(f"  Validation Accuracy: {accuracy_score(y_val, y_val_pred):.4f}")
    print(f"  Validation AUC-ROC: {roc_auc_score(y_val, y_val_proba):.4f}")
    models['Random Forest'] = rf_model

    # Logistic Regression
    print("\n[2/4] Training Logistic Regression...")
    lr_model = LogisticRegression(
        penalty='elasticnet',
        solver='saga',
        l1_ratio=0.5,
        max_iter=1000,
        random_state=RANDOM_STATE
    )
    lr_model.fit(X_train, y_train)
    y_val_pred = lr_model.predict(X_val)
    y_val_proba = lr_model.predict_proba(X_val)[:, 1]
    print(f"  Validation Accuracy: {accuracy_score(y_val, y_val_pred):.4f}")
    print(f"  Validation AUC-ROC: {roc_auc_score(y_val, y_val_proba):.4f}")
    models['Logistic Regression'] = lr_model

    # Support Vector Machine
    print("\n[3/4] Training Support Vector Machine...")
    svm_model = SVC(
        kernel='rbf',
        C=1.0,
        probability=True,
        random_state=RANDOM_STATE
    )
    svm_model.fit(X_train, y_train)
    y_val_pred = svm_model.predict(X_val)
    y_val_proba = svm_model.predict_proba(X_val)[:, 1]
    print(f"  Validation Accuracy: {accuracy_score(y_val, y_val_pred):.4f}")
    print(f"  Validation AUC-ROC: {roc_auc_score(y_val, y_val_proba):.4f}")
    models['SVM'] = svm_model

    # LightGBM
    print("\n[4/4] Training LightGBM...")
    lgb_model = lgb.LGBMClassifier(
        n_estimators=200,
        max_depth=7,
        learning_rate=0.05,
        random_state=RANDOM_STATE,
        n_jobs=-1
    )
    lgb_model.fit(X_train, y_train)
    y_val_pred = lgb_model.predict(X_val)
    y_val_proba = lgb_model.predict_proba(X_val)[:, 1]
    print(f"  Validation Accuracy: {accuracy_score(y_val, y_val_pred):.4f}")
    print(f"  Validation AUC-ROC: {roc_auc_score(y_val, y_val_proba):.4f}")
    models['LightGBM'] = lgb_model

    print("="*80)

    return models


In [19]:
# PHASE 9: MODEL EVALUATION
# =============================================================================

def evaluate_model(model, X_test, y_test, model_name='Model', scaler=None):
    """
    Comprehensive model evaluation on test set.

    Parameters:
    -----------
    model : trained model
        Model to evaluate
    X_test : DataFrame
        Test features
    y_test : Series
        Test labels
    model_name : str
        Name of the model
    scaler : StandardScaler, optional
        Scaler for neural network

    Returns:
    --------
    metrics : dict
        Evaluation metrics
    """
    print(f"\n{'='*80}")
    print(f"EVALUATING {model_name.upper()}")
    print(f"{'='*80}")

    # Scale if neural network
    if scaler is not None:
        X_test_eval = scaler.transform(X_test)
    else:
        X_test_eval = X_test

    # Predictions
    if hasattr(model, 'predict_proba'):
        y_pred_proba = model.predict_proba(X_test_eval)[:, 1]
        y_pred = (y_pred_proba >= 0.5).astype(int)
    else:
        # Neural network
        y_pred_proba = model.predict(X_test_eval).flatten()
        y_pred = (y_pred_proba >= 0.5).astype(int)

    # Calculate metrics
    accuracy = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred, zero_division=0)
    recall = recall_score(y_test, y_pred, zero_division=0)
    f1 = f1_score(y_test, y_pred, zero_division=0)
    auc_roc = roc_auc_score(y_test, y_pred_proba)
    mcc = matthews_corrcoef(y_test, y_pred)

    # Confusion matrix
    cm = confusion_matrix(y_test, y_pred)
    tn, fp, fn, tp = cm.ravel()

    specificity = tn / (tn + fp) if (tn + fp) > 0 else 0
    sensitivity = recall

    metrics = {
        'model_name': model_name,
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'sensitivity': sensitivity,
        'specificity': specificity,
        'f1_score': f1,
        'auc_roc': auc_roc,
        'mcc': mcc,
        'confusion_matrix': cm,
        'y_pred': y_pred,
        'y_pred_proba': y_pred_proba
    }

    # Print results
    print(f"\nTest Set Performance:")
    print(f"  Accuracy:    {accuracy:.4f} ({accuracy*100:.2f}%)")
    print(f"  Precision:   {precision:.4f}")
    print(f"  Recall:      {recall:.4f}")
    print(f"  Sensitivity: {sensitivity:.4f}")
    print(f"  Specificity: {specificity:.4f}")
    print(f"  F1-Score:    {f1:.4f}")
    print(f"  AUC-ROC:     {auc_roc:.4f}")
    print(f"  MCC:         {mcc:.4f}")

    print(f"\nConfusion Matrix:")
    print(f"  TN: {tn}  |  FP: {fp}")
    print(f"  FN: {fn}  |  TP: {tp}")

    # Compare to baseline
    baseline_accuracy = 0.70
    improvement = (accuracy - baseline_accuracy) / baseline_accuracy * 100

    print(f"\n Comparison to Baseline (70% accuracy):")
    if accuracy > baseline_accuracy:
        print(f"  ✓ IMPROVED by {improvement:.1f}%")
        print(f"  Absolute improvement: +{(accuracy - baseline_accuracy)*100:.1f} percentage points")
    else:
        print(f"  ✗ Below baseline by {abs(improvement):.1f}%")

    # Goal achievement
    print(f"\n Goal Achievement (>80% accuracy):")
    if accuracy >= 0.80:
        print(f"  GOAL ACHIEVED! Accuracy: {accuracy*100:.2f}%")
    else:
        gap = 0.80 - accuracy
        print(f"  Gap to goal: {gap*100:.1f} percentage points")

    print("="*80)

    return metrics


def plot_roc_curves(all_metrics, y_test, output_dir='results/figures'):
    """Plot ROC curves for multiple models."""
    print("\nGenerating ROC curves...")

    fig, ax = plt.subplots(figsize=(10, 8))

    for metrics in all_metrics:
        fpr, tpr, _ = roc_curve(y_test, metrics['y_pred_proba'])
        auc = metrics['auc_roc']
        ax.plot(fpr, tpr, lw=2, label=f"{metrics['model_name']} (AUC = {auc:.3f})")

    # Diagonal line
    ax.plot([0, 1], [0, 1], 'k--', lw=1, label='Chance (AUC = 0.500)')

    ax.set_xlabel('False Positive Rate', fontsize=12, fontweight='bold')
    ax.set_ylabel('True Positive Rate', fontsize=12, fontweight='bold')
    ax.set_title('ROC Curves - Model Comparison', fontsize=14, fontweight='bold')
    ax.legend(loc='lower right')
    ax.grid(True, alpha=0.3)

    plt.tight_layout()
    plt.savefig(f'{output_dir}/roc_curves.png', dpi=300, bbox_inches='tight')
    plt.close()

    print(f"  ROC curves saved to {output_dir}/roc_curves.png")


def plot_confusion_matrices(all_metrics, output_dir='results/figures'):
    """Plot confusion matrices for all models."""
    print("\nGenerating confusion matrices...")

    n_models = len(all_metrics)
    fig, axes = plt.subplots(2, (n_models + 1) // 2, figsize=(15, 10))
    axes = axes.flatten()

    for idx, metrics in enumerate(all_metrics):
        cm = metrics['confusion_matrix']
        sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', ax=axes[idx],
                   xticklabels=['Healthy', 'Condition'],
                   yticklabels=['Healthy', 'Condition'])
        axes[idx].set_title(f"{metrics['model_name']}\nAccuracy: {metrics['accuracy']:.3f}",
                           fontweight='bold')
        axes[idx].set_ylabel('True Label')
        axes[idx].set_xlabel('Predicted Label')

    # Hide unused subplots
    for idx in range(n_models, len(axes)):
        axes[idx].axis('off')

    plt.suptitle('Confusion Matrices - All Models', fontsize=16, fontweight='bold')
    plt.tight_layout()
    plt.savefig(f'{output_dir}/confusion_matrices.png', dpi=300, bbox_inches='tight')
    plt.close()

    print(f"  Confusion matrices saved to {output_dir}/confusion_matrices.png")


def create_performance_table(all_metrics, output_dir='results/tables'):
    """Create and save performance comparison table."""
    print("\nCreating performance comparison table...")

    # Create DataFrame
    table_data = []
    for metrics in all_metrics:
        table_data.append({
            'Model': metrics['model_name'],
            'Accuracy': f"{metrics['accuracy']:.4f}",
            'Precision': f"{metrics['precision']:.4f}",
            'Recall': f"{metrics['recall']:.4f}",
            'F1-Score': f"{metrics['f1_score']:.4f}",
            'AUC-ROC': f"{metrics['auc_roc']:.4f}",
            'MCC': f"{metrics['mcc']:.4f}"
        })

    df_table = pd.DataFrame(table_data)

    # Save as CSV
    df_table.to_csv(f'{output_dir}/model_performance.csv', index=False)

    # Save as LaTeX
    latex_table = df_table.to_latex(index=False, caption='Model Performance Comparison',
                                     label='tab:performance', float_format='%.4f')
    with open(f'{output_dir}/model_performance.tex', 'w') as f:
        f.write(latex_table)

    print(f"  Performance table saved to {output_dir}/")
    print("\n" + "="*80)
    print("MODEL PERFORMANCE SUMMARY")
    print("="*80)
    print(df_table.to_string(index=False))
    print("="*80)

    return df_table


In [20]:
# PHASE 10: MODEL INTERPRETABILITY (SHAP)
# =============================================================================

def shap_analysis(model, X_train, X_test, feature_names, model_name='XGBoost',
                  output_dir='results/figures'):
    """
    Perform SHAP analysis for model interpretability.

    Parameters:
    -----------
    model : trained model
        Model to interpret
    X_train : DataFrame
        Training data for background
    X_test : DataFrame
        Test data for explanations
    feature_names : list
        Names of features
    model_name : str
        Name of the model
    output_dir : str
        Output directory for figures

    Returns:
    --------
    shap_values : array
        SHAP values
    explainer : SHAP explainer
    """
    print("\n" + "="*80)
    print(f"PHASE 10: SHAP ANALYSIS - {model_name.upper()}")
    print("="*80)

    print("\n[1/4] Creating SHAP explainer...")

    # Select appropriate explainer
    if 'XGBoost' in model_name or 'LightGBM' in model_name or 'Random Forest' in model_name:
        explainer = shap.TreeExplainer(model)
        shap_values = explainer.shap_values(X_test)
    elif 'Neural Network' in model_name:
        # For Neural Network, use KernelExplainer with model.predict
        # Ensure X_test is scaled for NN if scaler was used during training
        # Assuming scaler is available in the main pipeline if NN is used
        # For KernelExplainer, using a background dataset is crucial for performance and accuracy
        background = shap.sample(X_train, min(100, len(X_train)))
        # Use model.predict for Keras models with sigmoid output
        explainer = shap.KernelExplainer(model.predict, background)
        # Limit X_test for KernelExplainer due to computational cost
        X_test_limited = X_test.sample(min(100, len(X_test)), random_state=RANDOM_STATE)
        shap_values = explainer.shap_values(X_test_limited)
    else:
        # For other models, use KernelExplainer with sample
        background = shap.sample(X_train, min(100, len(X_train)))
        explainer = shap.KernelExplainer(model.predict_proba, background)
        # Limit X_test for KernelExplainer due to computational cost
        X_test_limited = X_test.sample(min(100, len(X_test)), random_state=RANDOM_STATE)
        shap_values = explainer.shap_values(X_test_limited)


    print("  SHAP explainer created")

    # Handle multi-output SHAP values for binary classification
    if isinstance(shap_values, list):
        # For binary classification, shap_values is often a list [shap_values_class_0, shap_values_class_1]
        print("  Detected list of SHAP values (assuming binary classification). Using values for positive class.")
        shap_values_analysis = shap_values[1] # Typically index 1 is the positive class
    else:
        shap_values_analysis = shap_values

    # Check the shape of shap_values_analysis
    if shap_values_analysis.ndim != 2:
        print(f" Warning: SHAP values for analysis are not 2-dimensional (shape: {shap_values_analysis.shape}).")
        print("  Feature importance calculation might be affected.")


    # Global feature importance
    print("\n[2/4] Generating global feature importance plots...")

    # Calculate feature importance and ensure it's 1D
    feature_importance = np.abs(shap_values_analysis).mean(axis=0)
    # Ensure feature_importance is 1-dimensional regardless of previous shape
    feature_importance_1d = feature_importance.flatten()


    # Check if feature_importance_1d has the same length as feature_names
    if len(feature_importance_1d) != len(feature_names):
         print(f"  Error: Mismatch between number of calculated importances ({len(feature_importance_1d)}) and feature names ({len(feature_names)}). Skipping plots.")
         # Return empty or placeholder data if plotting is skipped
         return shap_values, explainer, pd.DataFrame(columns=['feature', 'importance'])


    plt.figure(figsize=(12, 10))
    # Ensure feature_names are passed correctly
    shap.summary_plot(shap_values, X_test, feature_names=feature_names,
                     max_display=20, show=False)
    plt.title(f'SHAP Summary Plot - {model_name}', fontsize=14, fontweight='bold', pad=20)
    plt.tight_layout()
    plt.savefig(f'{output_dir}/shap_summary_{model_name.replace(" ", "_")}.png',
                dpi=300, bbox_inches='tight')
    plt.close()

    # Bar plot
    plt.figure(figsize=(10, 8))
    # Ensure feature_names are passed correctly
    shap.summary_plot(shap_values, X_test, feature_names=feature_names,
                     plot_type='bar', max_display=20, show=False)
    plt.title(f'SHAP Feature Importance - {model_name}', fontsize=14, fontweight='bold', pad=20)
    plt.tight_layout()
    plt.savefig(f'{output_dir}/shap_importance_{model_name.replace(" ", "_")}.png',
                dpi=300, bbox_inches='tight')
    plt.close()

    print(f"  SHAP plots saved to {output_dir}/")

    # Top features analysis
    print("\n[3/4] Analyzing top important features...")

    importance_df = pd.DataFrame({
        'feature': feature_names,
        'importance': feature_importance_1d  # Use the flattened importance
    }).sort_values('importance', ascending=False)

    print("\n  Top 20 Most Important Features:")
    print(importance_df.head(20).to_string(index=False))

    # Save to CSV
    importance_df.to_csv(f'{output_dir}/../tables/shap_feature_importance_{model_name.replace(" ", "_")}.csv',
                        index=False)

    print("\n[4/4] Clinical interpretation...")
    print("\n  Key Microbial Biomarkers Identified:")

    # Identify top microbial features (exclude engineered features)
    microbial_features = importance_df[
        ~importance_df['feature'].str.contains('alpha_div|ratio|total|count|mean|std')
    ].head(10)

    for idx, row in microbial_features.iterrows():
        print(f"    {idx+1}. {row['feature'][:50]}")

    print("="*80)

    return shap_values, explainer, importance_df

In [21]:
# PHASE 11: ERROR ANALYSIS
# =============================================================================

def error_analysis(y_test, y_pred, y_pred_proba, X_test, feature_names):
    """
    Analyze misclassifications to identify patterns.

    Parameters:
    -----------
    y_test : array
        True labels
    y_pred : array
        Predicted labels
    y_pred_proba : array
        Prediction probabilities
    X_test : DataFrame
        Test features
    feature_names : list
        Feature names

    Returns:
    --------
    error_analysis_df : DataFrame
        Analysis of misclassified samples
    """
    print("\n" + "="*80)
    print("PHASE 11: ERROR ANALYSIS & MODEL REFINEMENT")
    print("="*80)

    # Identify misclassified samples
    misclassified = y_test != y_pred
    false_positives = (y_test == 0) & (y_pred == 1)
    false_negatives = (y_test == 1) & (y_pred == 0)

    print(f"\nMisclassification Summary:")
    print(f"  Total misclassified: {misclassified.sum()} ({misclassified.sum()/len(y_test)*100:.1f}%)")
    print(f"  False Positives: {false_positives.sum()}")
    print(f"  False Negatives: {false_negatives.sum()}")

    # Analyze false positives
    print("\n[1/2] Analyzing False Positives...")
    if false_positives.sum() > 0:
        fp_features = X_test[false_positives].mean()
        correct_neg_features = X_test[(y_test == 0) & (y_pred == 0)].mean()

        fp_diff = (fp_features - correct_neg_features).abs().sort_values(ascending=False)
        print(f"  Top features differing in False Positives:")
        for i, (feat, diff) in enumerate(fp_diff.head(10).items(), 1):
            print(f"    {i}. {feat[:40]}: {diff:.4f}")

    # Analyze false negatives
    print("\n[2/2] Analyzing False Negatives...")
    if false_negatives.sum() > 0:
        fn_features = X_test[false_negatives].mean()
        correct_pos_features = X_test[(y_test == 1) & (y_pred == 1)].mean()

        fn_diff = (fn_features - correct_pos_features).abs().sort_values(ascending=False)
        print(f"  Top features differing in False Negatives:")
        for i, (feat, diff) in enumerate(fn_diff.head(10).items(), 1):
            print(f"    {i}. {feat[:40]}: {diff:.4f}")

    # Prediction confidence analysis
    print("\n  Prediction Confidence Analysis:")
    correct_conf = y_pred_proba[~misclassified]
    incorrect_conf = y_pred_proba[misclassified]

    print(f"    Correct predictions - mean confidence: {np.abs(correct_conf - 0.5).mean():.3f}")
    print(f"    Incorrect predictions - mean confidence: {np.abs(incorrect_conf - 0.5).mean():.3f}")

    print("="*80)

    return misclassified, false_positives, false_negatives


In [22]:
# PHASE 12: RESULTS VISUALIZATION
# =============================================================================

def create_final_report(all_metrics, shap_importance, da_results, output_dir='results'):
    """
    Generate comprehensive results report.

    Parameters:
    -----------
    all_metrics : list
        List of metric dictionaries for all models
    shap_importance : DataFrame
        SHAP feature importance
    da_results : DataFrame
        Differential abundance results
    output_dir : str
        Output directory
    """
    print("\n" + "="*80)
    print("PHASE 12: GENERATING FINAL REPORT")
    print("="*80)

    report_path = f'{output_dir}/FINAL_RESULTS_REPORT.txt'

    with open(report_path, 'w') as f:
        f.write("="*80 + "\n")
        f.write("AI-POWERED GUT MICROBIOME CLASSIFIER FOR MENTAL HEALTH PREDICTION\n")
        f.write("FINAL RESULTS REPORT\n")
        f.write("="*80 + "\n\n")

        f.write(f"Generated: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}\n")
        f.write(f"Author: DSNVS Tejaswani Edupuganti\n")
        f.write(f"Module: 7151CEM - Computing Individual Research Project\n\n")

        f.write("="*80 + "\n")
        f.write("1. PROJECT OBJECTIVES & ACHIEVEMENT\n")
        f.write("="*80 + "\n\n")

        f.write("Primary Goal: Achieve >80% accuracy in mental health classification\n")
        f.write("Baseline to Beat: 70% (Valles-Colomer et al., 2019)\n\n")

        best_model = max(all_metrics, key=lambda x: x['accuracy'])
        f.write(f"BEST MODEL: {best_model['model_name']}\n")
        f.write(f"  Accuracy: {best_model['accuracy']*100:.2f}%\n")

        if best_model['accuracy'] >= 0.80:
            f.write("  PRIMARY GOAL ACHIEVED!\n")
        else:
            f.write(f"  Gap to 80% goal: {(0.80 - best_model['accuracy'])*100:.1f} percentage points\n")

        improvement = (best_model['accuracy'] - 0.70) / 0.70 * 100
        if improvement > 0:
            f.write(f"  Improvement over baseline: +{improvement:.1f}%\n")

        f.write("\n" + "="*80 + "\n")
        f.write("2. MODEL PERFORMANCE COMPARISON\n")
        f.write("="*80 + "\n\n")

        for metrics in sorted(all_metrics, key=lambda x: x['accuracy'], reverse=True):
            f.write(f"\n{metrics['model_name']}:\n")
            f.write(f"  Accuracy:    {metrics['accuracy']:.4f}\n")
            f.write(f"  Precision:   {metrics['precision']:.4f}\n")
            f.write(f"  Recall:      {metrics['recall']:.4f}\n")
            f.write(f"  F1-Score:    {metrics['f1_score']:.4f}\n")
            f.write(f"  AUC-ROC:     {metrics['auc_roc']:.4f}\n")
            f.write(f"  Specificity: {metrics['specificity']:.4f}\n")

        f.write("\n" + "="*80 + "\n")
        f.write("3. KEY MICROBIAL BIOMARKERS IDENTIFIED\n")
        f.write("="*80 + "\n\n")

        f.write("Top 20 Most Important Features (SHAP Analysis):\n\n")
        for idx, row in shap_importance.head(20).iterrows():
            f.write(f"  {idx+1}. {row['feature']}: {row['importance']:.4f}\n")

        f.write("\n" + "="*80 + "\n")
        f.write("4. DIFFERENTIALLY ABUNDANT TAXA\n")
        f.write("="*80 + "\n\n")

        sig_taxa = da_results[da_results['significant']].head(20)
        f.write(f"Significant taxa (FDR < 0.05): {len(sig_taxa)}\n\n")

        for idx, row in sig_taxa.iterrows():
            direction = "↑ Enriched" if row['log2_fold_change'] > 0 else "↓ Depleted"
            f.write(f"  {idx+1}. {row['feature'][:50]}\n")
            f.write(f"      {direction} in mental health condition\n")
            f.write(f"      Log2FC: {row['log2_fold_change']:.3f}, ")
            f.write(f"Adj. p-value: {row['p_adjusted']:.4e}\n\n")

        f.write("\n" + "="*80 + "\n")
        f.write("5. CLINICAL IMPLICATIONS\n")
        f.write("="*80 + "\n\n")

        f.write("This study demonstrates:\n\n")
        f.write("1. Machine learning models can effectively classify mental health\n")
        f.write("   conditions from gut microbiome data with high accuracy.\n\n")
        f.write("2. Specific microbial taxa show strong associations with depression\n")
        f.write("   and anxiety, supporting the gut-brain axis hypothesis.\n\n")
        f.write("3. SHAP analysis provides interpretable predictions that could guide\n")
        f.write("   personalized interventions and therapeutic strategies.\n\n")
        f.write("4. The identified biomarkers warrant further validation in\n")
        f.write("   prospective clinical studies.\n\n")

        f.write("="*80 + "\n")
        f.write("END OF REPORT\n")
        f.write("="*80 + "\n")

    print(f"\n Final report saved to {report_path}")
    print("="*80)


In [23]:
from datetime import datetime
import numpy as np
import pandas as pd
import joblib
import os

def main_pipeline(tsv_file=None, metadata_file=None, biom_file=None):
    """
    Execute complete microbiome → mental illness analysis pipeline.
    Parameters:
    -----------
    tsv_file : str, optional
        Path to abundance TSV file
    metadata_file : str
        Path to metadata TSV file
    biom_file : str, optional
        Path to BIOM file
    """
    print("\n" + "="*80)
    print("STARTING COMPLETE MICROBIOME MENTAL HEALTH ANALYSIS PIPELINE")
    print("="*80)
    print(f"Start time: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}\n")
    # -------------------------
    # Phase 1: Load abundance + metadata
    # -------------------------
    if biom_file:
        abundance_df, metadata_df = load_microbiome_data(tsv_file, metadata_file, biom_file)
    elif tsv_file:
        abundance_df = pd.read_csv(tsv_file, sep="\t", index_col=0)
        abundance_df.index = abundance_df.index.astype(str).str.strip()
    else:
        raise ValueError("Provide either BIOM file or TSV file for abundance data.")
    # Target variable
    TARGET_COLUMN = "mental_illness"
    if TARGET_COLUMN not in metadata_df.columns:
        raise ValueError(f"Target column '{TARGET_COLUMN}' not found in metadata.")
    # -------------------------
    # Phase 2: QC + preprocessing
    # -------------------------
    filtered_abundance, metadata_df, qc_stats = quality_control_filtering(abundance_df, metadata_df)  # <-- Updated: Pass and receive metadata_df
    normalized_abundance = normalize_microbiome_data(filtered_abundance, method='clr')
    # Labels
    labels = create_target_labels(metadata_df, TARGET_COLUMN)  # <-- Now uses filtered metadata_df
    common_samples = normalized_abundance.index.intersection(labels.index)
    normalized_abundance = normalized_abundance.loc[common_samples]
    labels = labels.loc[common_samples]
    # -------------------------
    # Phase 3: EDA
    # -------------------------
    alpha_div = calculate_alpha_diversity(filtered_abundance.loc[common_samples])
    plot_eda_summary(normalized_abundance, metadata_df.loc[common_samples],
                     labels, alpha_div)
    # -------------------------
    # Phase 4: Differential abundance
    # -------------------------
    da_results = differential_abundance_analysis(normalized_abundance, labels)
    if not da_results.empty and {'log2_fold_change', 'p_adjusted', 'significant'}.issubset(da_results.columns):
        plot_volcano_plot(da_results)
    else:
        print("\nSkipping volcano plot: insufficient DA results.")
    # -------------------------
    # Phase 5-6: Feature engineering + selection
    # -------------------------
    features_engineered = engineer_features(normalized_abundance, alpha_div)
    selected_features, X_selected = select_features(features_engineered, labels,
                                                    method='combined', k=50)
    # -------------------------
    # Phase 7-8: Train models
    # -------------------------
    data_splits = prepare_train_test_split(X_selected, labels)
    print("\n" + "="*80)
    print("TRAINING MODELS")
    print("="*80)
    xgb_model, _ = train_xgboost_model(data_splits['X_train'], data_splits['y_train'],
                                       data_splits['X_val'], data_splits['y_val'])
    nn_model, nn_history, nn_scaler = train_neural_network(data_splits['X_train'], data_splits['y_train'],
                                                           data_splits['X_val'], data_splits['y_val'])
    other_models = train_additional_models(data_splits['X_train'], data_splits['y_train'],
                                           data_splits['X_val'], data_splits['y_val'])
    # -------------------------
    # Phase 9: Evaluate models
    # -------------------------
    all_metrics = []
    xgb_metrics = evaluate_model(xgb_model, data_splits['X_test'],
                                 data_splits['y_test'], 'XGBoost')
    all_metrics.append(xgb_metrics)
    nn_metrics = evaluate_model(nn_model, data_splits['X_test'],
                                data_splits['y_test'], 'Neural Network', nn_scaler)
    all_metrics.append(nn_metrics)
    for name, model in other_models.items():
        metrics = evaluate_model(model, data_splits['X_test'], data_splits['y_test'], name)
        all_metrics.append(metrics)
    plot_roc_curves(all_metrics, data_splits['y_test'])
    plot_confusion_matrices(all_metrics)
    perf_table = create_performance_table(all_metrics)
    # -------------------------
    # Phase 10: SHAP analysis on best model
    # -------------------------
    best_model_idx = np.argmax([m['accuracy'] for m in all_metrics])
    best_model_name = all_metrics[best_model_idx]['model_name']
    best_model = {'XGBoost': xgb_model, 'Neural Network': nn_model, **other_models}[best_model_name]
    shap_importance = shap_analysis(best_model, data_splits['X_train'], data_splits['X_test'],
                                    selected_features, best_model_name)[2]
    # -------------------------
    # Phase 11-12: Error analysis + report
    # -------------------------
    error_analysis(data_splits['y_test'], all_metrics[best_model_idx]['y_pred'],
                   all_metrics[best_model_idx]['y_pred_proba'],
                   data_splits['X_test'], selected_features)
    create_final_report(all_metrics, shap_importance, da_results)
    # Save models + results
    os.makedirs('results/models', exist_ok=True)
    os.makedirs('results/tables', exist_ok=True)
    joblib.dump(xgb_model, 'results/models/xgboost_model.pkl')
    nn_model.save('results/models/neural_network_model.h5')
    joblib.dump(nn_scaler, 'results/models/nn_scaler.pkl')
    for name, model in other_models.items():
        joblib.dump(model, f'results/models/{name.replace(" ", "_").lower()}_model.pkl')
    da_results.to_csv('results/tables/differential_abundance.csv', index=False)
    shap_importance.to_csv('results/tables/shap_feature_importance.csv', index=False)
    pd.DataFrame({'feature': selected_features}).to_csv('results/tables/selected_features.csv', index=False)
    print("\nPipeline execution complete.")
    print(f"End time: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
    return {
        'models': {'xgboost': xgb_model, 'neural_network': nn_model, **other_models},
        'metrics': all_metrics,
        'best_model': best_model_name,
        'shap_importance': shap_importance,
        'da_results': da_results
    }

In [24]:
if __name__ == "__main__":

    # -------------------------
    # CONFIGURE FILE PATHS
    # -------------------------
    TSV_FILE = '/Users/gnanathejavalleri/Downloads/agp_mental_health.tsv'  # optional
    METADATA_FILE = '/Users/gnanathejavalleri/Downloads/agp_mental_health_metadata.tsv'
    BIOM_FILE = '/Users/gnanathejavalleri/Downloads/agp_mental_health.biom'  # preferred

    print("\n📁 INPUT FILES:")
    print(f"   • Abundance data (TSV): {TSV_FILE if TSV_FILE else 'Not provided'}")
    print(f"   • Metadata: {METADATA_FILE}")
    print(f"   • BIOM file: {BIOM_FILE if BIOM_FILE else 'Not provided'}")
    print("\n" + "="*80 + "\n")

    # -------------------------
    # OPTIONAL: Inspect files
    # -------------------------
    try:
        if TSV_FILE:
            print("🔍 Inspecting TSV file...")
            display(pd.read_csv(TSV_FILE, sep="\t", nrows=5))
        print("🔍 Inspecting metadata file...")
        display(pd.read_csv(METADATA_FILE, sep="\t", nrows=5))
    except Exception as e:
        print(f"⚠ Could not inspect files: {e}")

    # -------------------------
    # RUN PIPELINE
    # -------------------------
    try:
        results = main_pipeline(tsv_file=TSV_FILE, metadata_file=METADATA_FILE, biom_file=BIOM_FILE)

        print("\n✅ SUCCESS! Analysis completed successfully.")
        print("="*80)

        # Print summary
        print(f"\nBest Model: {results.get('best_model', 'N/A')}")
        if 'metrics' in results and results['metrics']:
            best_acc = max(m.get('accuracy', 0) for m in results['metrics'])
            print(f"Best Accuracy: {best_acc*100:.2f}%")

        # Optional: show label encoding
        if 'label_encoder' in results:
            le = results['label_encoder']
            print("\nLabel Encoding:", dict(zip(le.classes_, le.transform(le.classes_))))

    except Exception as e:
        print("\n❌ ERROR: Pipeline execution failed")
        print(f"Error message: {str(e)}")
        import traceback
        traceback.print_exc()

    print("\n" + "="*80)
    print("Thank you for using the Microbiome Mental Health Classifier!")
    print("="*80)



📁 INPUT FILES:
   • Abundance data (TSV): /Users/gnanathejavalleri/Downloads/agp_mental_health.tsv
   • Metadata: /Users/gnanathejavalleri/Downloads/agp_mental_health_metadata.tsv
   • BIOM file: /Users/gnanathejavalleri/Downloads/agp_mental_health.biom


🔍 Inspecting TSV file...


# Constructed from biom file
#OTU ID                                            10317.000001166.129660 10317.000001179.129117 10317.000001198.132370 10317.000001210.132352 10317.000001300.132352 10317.000001372.134169 10317.000001507.132012 10317.000001507.134787 10317.000001507.130365 10317.000001527.129338 10317.000001586.129660 10317.000001619.134787 10317.000001619.132012 10317.000001816.127185 10317.000001816.134169 10317.000002033.131034 10317.000002034.131034 10317.000002223.127185 10317.000002224.128356 10317.000002224.129293 10317.000002421.131034 10317.000002717.129609 10317.000002908.129099 10317.000002929.134307 10317.000002930.134307 10317.000003007.134169 10317.000003008.129636 10317.000003008.133774 10317.000003009.129660 10317.000003100.133896 10317.000003101.133896 10317.000003102.133896 10317.000003509.131186 10317.000003511.130519 10317.000003512.130519 10317.000003913.129117 10317.000003915.134750 10317.000004057.135163 10317.000004058.135163 10317.000004059.135163 10317.000004060.135163 10317.000004614.129117 10317.000004936.129636 10317.000004936.133774 10317.000004937.134169 10317.000004938.134169 10317.000005634.130778 10317.000005635.130778 10317.000005636.130778 10317.000005637.130778 10317.000005638.130778 10317.000005823.130519 10317.000005998.146205 10317.000006857.129099 10317.000007320.133464 10317.000007322.133464 10317.000007323.133464 10317.000007324.133464 10317.000007325.133464 10317.000007326.133464 10317.000007327.133464 10317.000007328.133464 10317.000007330.133464 10317.000007331.133464 10317.000007332.133464 10317.000007334.133464 10317.000009002.129660 10317.000009431.129099 10317.000009633.132012 10317.000009633.134787 10317.000009634.130067 10317.000010190.127185 10317.000010390.133464 10317.000010391.133464 10317.000010392.133464 10317.000010393.133464 10317.000010395.133464 10317.000010396.133464 10317.000010397.133464 10317.000010398.133464 10317.000010399.133464 10317.000010401.133464 10317.000010402.133464 10317.000010862.129660 10317.000010863.129660 10317.000011189.132796 10317.000011195.129338 10317.000011236.133896 10317.000011323.129117 10317.000011405.132111 10317.000011999.131186 10317.000012018.128285 10317.000012071.129293 10317.000012071.128356 10317.000012267.129099 10317.000012376.131186 10317.000012539.133464 10317.000012540.133464 10317.000012541.133464 10317.000012542.133464 10317.000012549.133464 10317.000012551.133464 10317.000012552.133464 10317.000012553.133464 10317.000012839.132118 10317.000012840.132118 10317.000012841.132118 10317.000012843.132118 10317.000012844.132118 10317.000012845.132118 10317.000012846.132118 10317.000012848.132118 10317.000012849.133464 10317.000012850.132118 10317.000012851.132118 10317.000012853.132118 10317.000013252.129573 10317.000013252.129368 10317.000013287.131314 10317.000013287.132111 10317.000013291.129099 10317.000013333.131330 10317.000013416.132012 10317.000013416.134787 10317.000013428.134750 10317.000013429.129660 10317.000013515.130067 10317.000013516.130067 10317.000013614.129293 10317.000013614.128356 10317.000013623.135163 10317.000013727.133896 10317.000013975.129636 10317.000013975.133774 10317.000014115.129338 10317.000014401.129636 10317.000014401.128356 10317.000014401.133774 10317.000014401.129293 10317.000014528.130067 10317.000014536.130519 10317.000014564.131034 10317.000014671.127185 10317.000014671.130530 10317.000014885.131885 10317.000014889.131000 10317.000014889.130365 10317.000014942.131186 10317.000014943.131186 10317.000014961.129117 10317.000015307.129099 10317.000015308.129099 10317.000015309.129099 10317.000015310.129338 10317.000015573.131885 10317.000015574.130519 10317.000015601.129338 10317.000015825.135163 10317.000015861.129573 10317.000015938.135163 10317.000016169.134307 10317.000016349.130365 10317.000016350.128356 10317.000016350.129293 10317.000016350.129609 10317.000016373.146205 10317.000016493.134307 10317.000017138.134307 10317.000017155.129660 10317.000017272.133774 10317.0000

🔍 Inspecting metadata file...


#SampleID      milk_substitute_frequency seasonal_allergies  \
0  10317.000001                          Never                 No   
1  10317.000001                          Never                 No   
2  10317.000001                          Never                 No   
3  10317.000001                          Never                 No   
4  10317.000001  Occasionally (1-2 times/week)                Yes   

                          cdiff  allergic_to_peanuts  \
0  I do not have this condition                False   
1  I do not have this condition                False   
2  I do not have this condition                False   
3  I do not have this condition                False   
4  I do not have this condition                False   

        artificial_sweeteners dog  specialized_diet_exclude_dairy  \
0  Rarely (a few times/month)  No                           False   
1                       Never  No                           False   
2                       Never  No                            True   
3                       Never  No                           False   
4                       Never  No                           False   

        prepared_meals_frequency acne_medication  ...  \
0  Occasionally (1-2 times/week)              No  ...   
1  Occasionally (1-2 times/week)              No  ...   
2                          Never              No  ...   
3  Occasionally (1-2 times/week)              No  ...   
4                          Never              No  ...   

  other_supplement_frequency  livingwith specialized_diet_exclude_nightshades  \
0                         No          No                                False   
1                        Yes          No                                False   
2                        Yes          No                                False   
3                        Yes          No                                False   
4                        Yes          No                                False   

  env_material specialized_diet_other_restrictions_not_described_here  \
0        feces                                              False       
1       saliva                                              False       
2        feces                                               True       
3        feces                                              False       
4        feces                                              False       

   ready_to_eat_meals_frequency cancer_treatment  \
0  Rarely (less than once/week)     not provided   
1                         Never     not provided   
2                         Never     not provided   
3  Rarely (less than once/week)     not provided   
4                         Never     not provided   

                              bowel_movement_quality  \
0  I tend to have normal formed stool - Type 3 and 4   
1  I tend to be constipated (have difficulty pass...   
2  I tend to have diarrhea (watery stool) - Type ...   
3  I tend to have diarrhea (watery stool) - Type ...   
4  I tend to be constipated (have difficulty pass...   

         sugary_sweets_frequency nail_biter  
0  Occasionally (1-2 times/week)        Yes  
1   Rarely (less than once/week)         No  
2                          Never         No  
3  Occasionally (1-2 times/week)         No  
4                          Never         No  

[5 rows x 159 columns]


STARTING COMPLETE MICROBIOME MENTAL HEALTH ANALYSIS PIPELINE
Start time: 2025-11-20 00:25:33


PHASE 1: DATA LOADING & INTEGRATION

[1/3] Loading from BIOM file: /Users/gnanathejavalleri/Downloads/agp_mental_health.biom...
✓ Loaded BIOM table: 20509 samples × 214483 features
  Sample IDs after cleanup (first 5): ['10317.000001166.129660', '10317.000001179.129117', '10317.000001198.132370', '10317.000001210.132352', '10317.000001300.132352']

[2/3] Loading metadata from /Users/gnanathejavalleri/Downloads/agp_mental_health_metadata.tsv...
✓ Loaded metadata: 23588 samples × 158 variables

[3/3] Aligning samples...
  Common samples found: 17723

PHASE 1 COMPLETE: 17723 samples × 214483 features

PHASE 2: QUALITY CONTROL & PREPROCESSING

Initial data dimensions:
 Samples: 19302
 Features: 214483

[1/3] Filtering samples with <1000 reads...
 Removed 574 samples, remaining 18728

[2/3] Filtering features present in <1.0% of samples...
 Remaining features after prevalence filter: 1551

[3/3] 

...

 Total params: 56,065 (219.00 KB)

 Trainable params: 55,169 (215.50 KB)

 Non-trainable params: 896 (3.50 KB)


[2/3] Training model...
Epoch 1/100
626/626 ━━━━━━━━━━━━━━━━━━━━ 2s 957us/step - accuracy: 0.5945 - auc: 0.6279 - loss: 0.7000 - val_accuracy: 0.5970 - val_auc: 0.5819 - val_loss: 0.6674 - learning_rate: 0.0010
Epoch 2/100
626/626 ━━━━━━━━━━━━━━━━━━━━ 0s 688us/step - accuracy: 0.6543 - auc: 0.7094 - loss: 0.6247 - val_accuracy: 0.6129 - val_auc: 0.5766 - val_loss: 0.6645 - learning_rate: 0.0010
Epoch 3/100
626/626 ━━━━━━━━━━━━━━━━━━━━ 0s 688us/step - accuracy: 0.6936 - auc: 0.7570 - loss: 0.5863 - val_accuracy: 0.6280 - val_auc: 0.5801 - val_loss: 0.6553 - learning_rate: 0.0010
Epoch 4/100
626/626 ━━━━━━━━━━━━━━━━━━━━ 0s 687us/step - accuracy: 0.7159 - auc: 0.7877 - loss: 0.5556 - val_accuracy: 0.6474 - val_auc: 0.5804 - val_loss: 0.6543 - learning_rate: 0.0010
Epoch 5/100
626/626 ━━━━━━━━━━━━━━━━━━━━ 0s 685us/step - accuracy: 0.7356 - auc: 0.8113 - loss: 0.5303 - val_accuracy: 0.6734 - val_auc: 0.5774 - val_loss: 0.6226 - learning_rate: 0.0010
Epoch 6/100
626/626 ━━━━━━━━━━━━━━━━━━━━

  SHAP plots saved to results/figures/

[3/4] Analyzing top important features...

  Top 20 Most Important Features:
                                                                                   feature  importance
                                                                             feature_count    0.442943
                                                                        alpha_div_observed    0.245080
                                                                             std_abundance    0.163442
TACGGAAGGTCCGGGCGTTATCCGGATTTATTGGGTTTAAAGGGAGCGTAGGCCGGAGATTAAGCGTGTTGTGAAATGTAGATGCTCAAC    0.123105
TACGTAGGTGGCAAGCGTTGTCCGGATTTACTGGGTGTAAAGGGCGTGTAGCCGGGAAGGCAAGTCAGATGTGAAATCCACGGGCTTAAC    0.101965
TACGGAGGATCCGAGCGTTATCCGGATTTATTGGGTTTAAAGGGAGCGTAGGTGGACAGTTAAGTCAGTTGTGAAAGTTTGCGGCTCAAC    0.093556
AACGTAGGTCACAAGCGTTGTCCGGAATTACTGGGTGTAAAGGGAGCGCAGGCGGGAAGACAAGTTGGAAGTGAAATCTATGGGCTCAAC    0.085260
TACGGAGGATTCAAGCGTTATCCGGATTTATTGGGTTTAAAGGGTGCGTAGGCGGTTTG